# LDA Topic Modelling

* This notebook is showcases the process of building an NLP Topic Model using `Latent Dirichlet Allocation` method. 
* The dataset we are going to use are `title` and `soft title` from `apify_dataset_clean.csv`. 

## Table Of Contents

## Installations


In [1]:
# ## installing required libraries
! pip install beautifulsoup4
! pip install pandas
! pip install numpy
! pip install plotly
! pip install nbformat
! pip install ipykernel
! pip install matplotlip
! pip install wordcloud
! pip install gensim
! pip install pyLDAvis
! pip install nltk
! pip install -U pip setuptools wheel
! pip install -U spacy
! python -m spacy download en_core_web_trf 


[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


...

  Using cached pip-22.3.1-py3-none-any.whl (2.1 MB)
  Using cached setuptools-65.6.3-py3-none-any.whl (1.2 MB)
  Using cached wheel-0.38.4-py3-none-any.whl (36 kB)


ERROR: To modify pip, please run the following command:
D:\workspace\Aletheia\env\Scripts\python.exe -m pip install -U pip setuptools wheel

[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


     -------------------------------------- 460.3/460.3 MB 7.4 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_trf')



[notice] A new release of pip available: 22.2.2 -> 22.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


## Imports

In [2]:
import pandas as pd
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

import re
import string
from bs4 import BeautifulSoup
import nltk
from nltk.stem import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
nltk.download('stopwords')
from pprint import pprint

import spacy
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.model_selection import GridSearchCV

from gensim import corpora, models
from gensim.utils import simple_preprocess
from gensim.models import Phrases
from gensim.models.phrases import Phraser
from gensim.models import CoherenceModel
from gensim.models.ldamodel import LdaModel
from gensim.models.ldamulticore import LdaMulticore

# Plotting tools
import pyLDAvis
import pyLDAvis.sklearn
import pyLDAvis.gensim_models as gensimvis
import matplotlib.pyplot as plt
%matplotlib inline

import plotly.express as px
import plotly.graph_objects as go
import plotly.io as io

# loading library
import pickle

from joblib import dump, load

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\gaura\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
d:\workspace\Aletheia\env\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
d:\workspace\Aletheia\env\lib\site-packages\past\builtins\misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib and slated for removal in Python 3.12; see the module's documentation for alternative uses
  from imp import reload


## Reading Data

In [3]:
## reading manaully scrapped data
data = pd.read_csv('../data/apify_dataset_clean.csv')
print(data.shape)

(11003, 13)


## Utility Functions

### Preparing Stop Words

In [4]:
## extending stopwords
# lets break down the cleaning functions into smaller functions
stop_words = nltk.corpus.stopwords.words('english')

## trying to remove stopwords from stopwords super set. 
stopwords_super_set = pd.read_csv("../data/stopwords/sw1k.csv")

## filtering stopwords to pronouns and other type
stopwords_to_remove = list(stopwords_super_set.loc[(stopwords_super_set["type"] == "G" ), "term"])


# stop_words.extend(['from', 'subject', 're', 'edu', 'use', 'say', 'one', 'time', 'people',
#                   'know', 'like', 'tell', 'get', 'year', 'go', 'around', 'award', 'actually', 'carry',
#                    'new', 'it', 'show', 'news', 'go', 'fox', 'make', 'do', 'not', 'say',
#                    'also', 'love', 'it', 'star', 'go', 'do', 'say', 'not', 'said'
#                    ])

# stop_words.extend(stopwords_to_remove)
print(stop_words)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

### Common Utility Functions

In [5]:
nlp = spacy.load('en_core_web_trf')
# Utility Functions for Text Cleaning
def sent_to_words(sentences):
    for sentence in sentences:
        yield (simple_preprocess(str(sentence), deacc=True))

# function to clean html tags from text


def clean_html(html):
    # parse html content
    soup = BeautifulSoup(html, "html.parser")
    for data in soup(['style', 'script', 'code', 'a']):
        # Remove tags
        data.decompose()
    # return data by retrieving the tag content
    return ' '.join(soup.stripped_strings)

# function to convert text to lowercase


def lower_case(text):
    return text.lower()

# function to remove line breaks


def remove_line_breaks(text):
    return re.sub(r'\n', '', text)

# function to remove punctuation


def remove_punctuation(text):
    return text.translate(str.maketrans('', '', string.punctuation))

# function to remove numbers


def remove_numbers(text):
    return re.sub(r'\d+', '', text)

# function to remove extra spaces


def remove_extra_spaces(text):
    return re.sub(' +', ' ', text)

# function to remove stopwords


def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

# helper function to create pos tags


def create_pos_tag(str_sent):
    return nlp(str_sent)

# function for text lemmatization using spac
##'ADJ', 'VERB'
def lemmatization(texts, allowed_postags=['PROPN', 'NOUN']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent))
        texts_out.append(
            [token.lemma_ for token in doc if (token.pos_ in allowed_postags and token.is_alpha and token.is_stop == False)])
    return texts_out

def lemmatization_without_pos(texts):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent))
        texts_out.append(
            [token.lemma_ for token in doc])
    return texts_out


def make_bigrams(texts, bigram_mod):
    return [bigram_mod[doc] for doc in texts]


def make_trigrams(texts, bigram_mod, trigram_mod):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

## helper function to create pos tags distribution
def create_pos_tags_distribution(docs = []):
    token_distribution = {}
    is_alpha = 0
    is_stop = 0
    for doc in docs:
        for token in doc:
            token_distribution[token.pos_] = token_distribution.get(token.pos_, 0) + 1
            if(token.is_alpha):
                is_alpha += 1
            if(token.is_stop):
                is_stop += 1
    return token_distribution, is_alpha, is_stop


# function to create n-grams from noun chunks
def create_noun_chunk_ngrams(docs):
    n_gram_docs = []
    for doc in docs:
        doc_text = doc.text
        for chunk in doc.noun_chunks:
            chunk_n_gram = "_".join(chunk.text.split(" "))
            doc_text = doc_text.replace(chunk.text, chunk_n_gram)
        n_gram_docs.append(doc_text.split(" "))
    return n_gram_docs


def lemmatization_noun_chunks(texts):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent))
        texts_out.append([token.lemma_ for token in doc if (
            ("_" in token.text) or ## if the token is a noun chunk allow that
            (token.pos_ in ['NOUN', 'PROPN'] and token.is_alpha and token.is_stop == False) ## if the token is a noun or proper noun allow that
        )])
    return texts_out

### Gensim Models Utility Functions

In [6]:
## function to compute optimal parameters for LDA model
def compute_coherence_values(dictionary, corpus, id2word, texts, num_topics, passes, chunk_sizes=[200]):
    """
    Compute c_v coherence for various number of topics

    Parameters:
    ----------
    dictionary : Gensim dictionary
    corpus : Gensim corpus
    texts : List of input texts
    limit : Max num of topics

    Returns:
    -------
    model_list : List of LDA topic models
    coherence_values : Coherence values corresponding to the LDA model with respective number of topics
    """
    coherence_values = []
    model_list = []
    params = []
    for num_topic in num_topics:
        for chunk_size in chunk_sizes:
            for num_passes in passes:
                model = LdaModel(corpus=corpus,
                                 id2word=id2word,
                                 num_topics=num_topic,
                                 random_state=100,
                                 update_every=1,
                                 chunksize=chunk_size,
                                 passes=num_passes,
                                 per_word_topics=True)
                model_list.append(model)
                coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
                coherence_lda = coherencemodel.get_coherence()
                coherence_values.append(coherence_lda)
                params.append({'num_topics': num_topic, 'chunk_size': chunk_size, 'passes': num_passes})

    return model_list, coherence_values, params

def analyze_gensim_lda_model(lda_model, corpus, id2word, texts, num_topics, passes, chunk_sizes=[200]):
    # Compute Perplexity
    print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.
    # Compute Coherence Score
    coherence_model_lda = CoherenceModel(model=lda_model, texts=texts, dictionary=id2word, coherence='c_v')
    coherence_lda = coherence_model_lda.get_coherence()
    print('\nCoherence Score: ', coherence_lda)

## helper functions to visualize LDA model
def visualize_gensim_lda_model(lda_model, corpus, id2word, filename="gensim_lda.html"):
    # Visualize the topics
    pyLDAvis.enable_notebook()
    vis = gensimvis.prepare(lda_model, corpus, id2word)
    vis.save(filename)

### Sklearn Model Utility Functions

In [7]:
import numpy as np


# Styling
def color_green(val):
    color = 'green' if val > .1 else 'black'
    return 'color: {col}'.format(col=color)

def make_bold(val):
    weight = 700 if val > .1 else 400
    return 'font-weight: {weight}'.format(weight=weight)


def print_sklearn_sparcity(data_vectorized):
    # Materialize the sparse data
    data_dense = data_vectorized.todense()

    # Compute Sparsicity = Percentage of Non-Zero cells
    print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")


def create_sklearn_dominent_topic_dataframe(lda_model, data_vectorized):
    lda_output = lda_model.transform(data_vectorized)
    # column names
    topicnames = ["Topic" + str(i) for i in range(lda_model.n_components)]
    # index names
    docnames = ["Doc" + str(i) for i in range(len(data))]
    
    df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topicnames, index=docnames)
    # Get dominant topic for each document
    dominant_topic = np.argmax(df_document_topic.values, axis=1)
    df_document_topic['dominant_topic'] = dominant_topic
    return df_document_topic

def print_sklearn_dominant_topics(lda_model, data_vectorized):
    df_document_topic = create_sklearn_dominent_topic_dataframe(lda_model, data_vectorized)
    # Apply Style
    df_document_topics = df_document_topic.head(15).style.applymap(color_green).applymap(make_bold)
    return df_document_topics

def print_sklearn_topic_distribution(lda_model, data_vectorized):
    df_document_topic = create_sklearn_dominent_topic_dataframe(lda_model, data_vectorized)
    df_topic_distribution = df_document_topic['dominant_topic'].value_counts().reset_index(name="Num Documents").rename(columns={'index':'Topic'})
    # df_topic_distribution.columns = ["Topic Num", "Num Documents"]
    return df_topic_distribution


# Show top n keywords for each topic
def show_sklearn_topics(vectorizer, lda_model, n_words=20):
    keywords = np.array(vectorizer.get_feature_names_out())
    topic_keywords = []
    for topic_weights in lda_model.components_:
        top_keyword_locs = (-topic_weights).argsort()[:n_words]
        topic_keywords.append(keywords.take(top_keyword_locs))
    return topic_keywords

def format_sklearn_topics(topic_keywords):
    df_topic_keywords = pd.DataFrame(topic_keywords)
    df_topic_keywords.columns = ['Word '+str(i) for i in range(df_topic_keywords.shape[1])]
    df_topic_keywords.index = ['Topic '+str(i) for i in range(df_topic_keywords.shape[0])]
    return df_topic_keywords

def analyze_sklearn_lda_model(lda_model, data_vectorized):
    # Log Likelyhood: Higher the better
    print("Log Likelihood: ", lda_model.score(data_vectorized))
    # Perplexity: Lower the better. Perplexity = exp(-1. * log-likelihood per word)
    print("Perplexity: ", lda_model.perplexity(data_vectorized))

## helper function to visualize lda model
def visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer, mds='tsne'):    
    pyLDAvis.enable_notebook()
    panel2 = pyLDAvis.sklearn.prepare(lda_model, data_vectorized, vectorizer, mds=mds)
    return panel2

## Text Pre-processing

In [8]:
def preprocess_text(text):
     text = clean_html(text)
     text = lower_case(text)
     text = remove_line_breaks(text)
     text = remove_punctuation(text)
     text = remove_numbers(text)
     text = remove_extra_spaces(text)
     return text

data["cleaned_soft_title"] = data["soft_title"].apply(preprocess_text)

d:\workspace\Aletheia\env\lib\site-packages\bs4\__init__.py:435: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  warnings.warn(


### Tokenizing

In [9]:
data_words = list(sent_to_words(data['cleaned_soft_title']))

## EDA on Title Data

In [10]:
## quick and dirty test to see if we should use `title` or `soft_title` column. Using the longer column assuming it has more data. 
data[data['title'].str.len() > data["soft_title"].str.len()]


Empty DataFrame
Columns: [url, author, date, title, soft_title, description, text, day, month, year, month_name, word_count, line_count, cleaned_soft_title]
Index: []

In [11]:
## check for duplicates
data["soft_title"].duplicated().sum()

3284

In [12]:
## there are 3287 duplicates in soft_title. But the URLs are different. But since we are using soft_title for topic modelling, we will remove duplicates

data.drop_duplicates(subset ="soft_title", inplace = True)

In [13]:
## sanity checking for duplicates
data["soft_title"].duplicated().sum()

0

In [14]:
data['title_word_count'] = data['soft_title'].apply(lambda x: len(str(x).split(" ")))

data['title_word_count'].describe()


count    7719.000000
mean       13.107397
std         2.846463
min         3.000000
25%        11.000000
50%        13.000000
75%        15.000000
max        23.000000
Name: title_word_count, dtype: float64

##### Notes
* Couple of interesting outliers, a title with 23 words and 4 words. 
* Lets check them out. 

In [15]:
## checkout outliers 
data[data["title_word_count"] > 15]["title"]

0        Biden says after Xi meeting he doesn’t believe...
3        Katie Hobbs defeats GOP challenger Kari Lake, ...
15       On this day in history, Nov. 15, 1956, Elvis m...
16       Walker hauls in $11 million since start of Geo...
20       Having sized up Biden, Putin invaded Ukraine. ...
                               ...                        
10982    Serena and Venus Williams lose what may be fin...
10986    Ye gets slammed by rapper Meek Mill after Tuck...
10988    Novak Djokovic points to 'positive signs' ahea...
10994    Erie County DA says domestic terrorism charges...
10996    Wimbledon fan takes legal action after Nick Ky...
Name: title, Length: 1607, dtype: object

In [16]:
## checking the distribution of word count in title
fig = px.histogram(data, x="title_word_count", title="Distribution of Word Count in Title")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



##### Notes
* Word counts are fairly distributed. 

In [17]:
## lets create POS tags for each title and see the distribution of POS tags
# docs = [nlp(text) for text in data['soft_title']]
docs = data["soft_title"].apply(create_pos_tag)

In [18]:
## creating pos tags distribution
token_distribution, is_alpha, is_stop = create_pos_tags_distribution(docs)

In [19]:
## convert the dictionary to a dataframe
token_distribution_df = pd.DataFrame.from_dict(token_distribution, orient='index', columns=['count']).reset_index().rename(columns={"index": "tags"})


In [20]:
## lets create a distribution of POS tags
## checking the distribution of word count in title
fig = px.histogram(token_distribution_df, x="tags", y="count", title="Distribution POS Tags in Title")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [21]:
## lets see how many words are alpha and how many are stop words
print(f"we have total {data['title_word_count'].sum()} words in the title. Out of which {is_alpha} are alpha and {is_stop} are stop words")

we have total 101176 words in the title. Out of which 100416 are alpha and 29908 are stop words


##### Notes
* So `maximum` tags are
    * `PROPN`- proper noun
    * `VERB` - verb
    * `ADP` - adposition
    * `NOUN` - noun
    * `PUNCT` - punctuation
    * `ADJ` - adjective
* Since these are news article titles, I think useful tags are, 
    * `PROPN`
    * `NOUN`
    * `VERB`
    * `ADJ` - Not sure about adjective yet. 
* We can remove rest of the words and still have a decent topic model. 
* We can also use the `is_stop` and `is_alpha` tags to remove the stopwords and non alpha tokens.
    * Lets update the helper functions accordingly. 

### Word Frequency

In [24]:
from collections import Counter
# lets see if we can calculate word frequency
# all tokens that arent stop words or punctuations
words = []
for doc in docs:
    doc_words = [token.text for token in doc if token.pos_ in ['PROPN', 'NOUN'] and not token.is_stop and not token.is_punct and token.is_alpha]
    words.append(doc_words)

flat_list = [item for sublist in words for item in sublist]


word_counts = Counter(flat_list)
word_counts.most_common(10)


[('Biden', 765),
 ('Trump', 334),
 ('GOP', 306),
 ('House', 276),
 ('Senate', 220),
 ('Ukraine', 215),
 ('Democrats', 200),
 ('election', 197),
 ('race', 196),
 ('New', 185)]

In [25]:
## lets try and plot the word cloud
word_counts_df = pd.DataFrame.from_dict(word_counts, orient='index', columns=['count']).reset_index().rename(columns={"index": "word"})

fig = px.histogram(word_counts_df, x="word", y="count", title="Distribution POS Tags in Title")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [26]:
word_counts_df.describe()

count
count  9184.000000
mean      5.451982
std      15.890459
min       1.000000
25%       1.000000
50%       2.000000
75%       4.000000
max     765.000000

##### Notes
* Interesting the difference between `mean` and `max` frequency is quick big.  Wonder if that would cause issues in the model. 

## Creating Bigram & Tigram Models

In [28]:
# Build the bigram and trigram models
bigram = Phrases(data_words, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = Phrases(bigram[data_words], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = Phraser(bigram)
trigram_mod = Phraser(trigram)

# See trigram example
print(trigram_mod[bigram_mod[data_words[10]]])

['biden', 'says', 'after', 'xi', 'meeting', 'he', 'doesn', 'believe', 'there', 'is', 'imminent', 'attempt', 'from', 'china', 'to', 'invade_taiwan']


## Gensim LDA with BOW

### Lemmatization

In [30]:
# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'attempt', 'china', 'taiwan']]


### Create Dictionary & Corpus

In [49]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)
## filter out words that occur less than 10 documents, or more than 75% of the documents.
id2word.filter_extremes(no_below=30, no_above=0.75, keep_n=10000)
# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 1), (2, 1), (3, 1)]]


In [50]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]


[[('biden', 1), ('china', 1), ('meeting', 1), ('taiwan', 1)]]

### Building the Topic Model

In [58]:
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=50,
                     random_state=100,
                     update_every=1,
                     chunksize=200,
                     passes=200,
                    #  alpha='auto',
                     per_word_topics=True)


In [59]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
# doc_lda = lda_model[corpus]

[(34,
  '0.147*"office" + 0.146*"team" + 0.119*"harry" + 0.110*"jeff" + '
  '0.110*"mother" + 0.096*"tom" + 0.085*"prince" + 0.061*"king" + '
  '0.054*"warnock" + 0.054*"charles"'),
 (15,
  '0.377*"afghanistan" + 0.318*"leader" + 0.278*"country" + 0.000*"right" + '
  '0.000*"philadelphia" + 0.000*"plan" + 0.000*"abbott" + 0.000*"gun" + '
  '0.000*"arrest" + 0.000*"player"'),
 (48,
  '0.436*"bidens" + 0.262*"speech" + 0.261*"nation" + 0.000*"philadelphia" + '
  '0.000*"gun" + 0.000*"mcconnell" + 0.000*"abbott" + 0.000*"bus" + '
  '0.000*"candidate" + 0.000*"probe"'),
 (20,
  '0.558*"texas" + 0.160*"fire" + 0.148*"dog" + 0.103*"call" + 0.000*"plan" + '
  '0.000*"right" + 0.000*"abbott" + 0.000*"bus" + 0.000*"philadelphia" + '
  '0.000*"force"'),
 (27,
  '0.443*"police" + 0.279*"man" + 0.203*"time" + 0.063*"chicago" + 0.000*"gun" '
  '+ 0.000*"bus" + 0.000*"philadelphia" + 0.000*"mcconnell" + 0.000*"plan" + '
  '0.000*"arrest"'),
 (26,
  '0.311*"death" + 0.234*"iran" + 0.159*"kid" + 0.099

### Analyzing Model

In [60]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -27.651664681438202

Coherence Score:  0.6269241527911427


### Visualize Topics

In [61]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.



PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
7     -0.124194  0.021893       1        1  3.714727
40    -0.032886  0.024100       2        1  3.657658
35    -0.072352  0.027066       3        1  3.575053
45    -0.071434 -0.385268       4        1  3.428881
30    -0.035586  0.023139       5        1  3.042836
33    -0.052758  0.020044       6        1  2.864114
41    -0.079560  0.019396       7        1  2.756753
29    -0.082975  0.017906       8        1  2.720131
13    -0.057586  0.015741       9        1  2.661351
27    -0.090926  0.021173      10        1  2.617957
23    -0.064425  0.017636      11        1  2.557267
42    -0.077638  0.018111      12        1  2.545989
26    -0.057606  0.021111      13        1  2.513205
5     -0.043606  0.020026      14        1  2.476739
49     0.001837  0.018702      15        1  2.471320
3     -0.035585  0.017558      16        1  2.429182
16    -0.065710  0.016823      17        1  2.403133
9     -0.053517  0.018619      18        1  2.388705
47    -0.054312  0.015229      19        1  2.342893
2     -0.060349  0.023941      20        1  2.301562
34    -0.006229  0.017569      21        1  2.221926
24    -0.058190  0.015858      22        1  1.999343
25    -0.061375  0.017504      23        1  1.973175
1     -0.059152  0.014757      24        1  1.879242
22    -0.016907  0.013693      25        1  1.863259
12    -0.030877  0.015441      26        1  1.834023
38    -0.006134 -0.302482      27        1  1.791523
11    -0.050346  0.015113      28        1  1.776865
32    -0.032912  0.014308      29        1  1.732147
0     -0.024783  0.013329      30        1  1.717222
14    -0.026800  0.013450      31        1  1.706253
39    -0.018032  0.009996      32        1  1.705944
8     -0.026263  0.012556      33        1  1.636122
17    -0.045508  0.011972      34        1  1.622804
20    -0.024573  0.012318      35        1  1.610460
31    -0.003484  0.010381      36        1  1.565628
19    -0.014846  0.012328      37        1  1.541646
4     -0.024957  0.011371      38        1  1.520204
15    -0.046035  0.013413      39        1  1.483900
43    -0.058323  0.015810      40        1  1.415980
10     0.008501  0.010701      41        1  1.402113
37     0.031440  0.008555      42        1  1.399018
48    -0.002437  0.009885      43        1  1.364091
46    -0.010135  0.009480      44        1  1.268926
21     0.113234  0.004933      45        1  1.133850
28     0.341258  0.000963      46        1  0.672976
18     0.341258  0.000963      47        1  0.672976
44     0.341258  0.000963      48        1  0.672976
6      0.341258  0.000963      49        1  0.672976
36     0.341258  0.000963      50        1  0.672976, topic_info=          Term         Freq        Total Category  logprob  loglift
0        biden  1264.000000  1264.000000  Default  30.0000  30.0000
6          gop   611.000000   611.000000  Default  29.0000  29.0000
5     election   575.000000   575.000000  Default  28.0000  28.0000
7        house   587.000000   587.000000  Default  27.0000  27.0000
132     senate   576.000000   576.000000  Default  26.0000  26.0000
..         ...          ...          ...      ...      ...      ...
25      newsom     0.521734    56.515781  Topic50  -6.1633   0.3161
26   weinstein     0.521734    60.585765  Topic50  -6.1633   0.2466
27   commander     0.521734    46.811898  Topic50  -6.1633   0.5045
28        loss     0.521734    79.719340  Topic50  -6.1633  -0.0279
29      season     0.521734    86.979578  Topic50  -6.1633  -0.1151

[2800 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
34       32  0.991259  abortion
34       46  0.002179  abortion
34       47  0.002179  abortion
34       48  0.002179  abortion
34       49  0.002179  abortion
...     ...       ...       ...
165      46  0.004071      york
165      47  0.004071      york
165      48  0.004071      

## Gensim LDA with Bigram BOW

### Lemmatization

In [52]:
## lemmatization with bigrams
data_words_bigrams = make_bigrams(data_words, bigram_mod)

# data_words_trigrams = make_trigrams(data_words, bigram_mod, trigram_mod)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
# nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
# data_lemmatized = lemmatization(data_words_bigrams)
data_lemmatized = lemmatization_noun_chunks(data_words_bigrams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'attempt', 'china', 'taiwan']]


### Create Dictionary & Corpus

In [53]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1)]]


In [54]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]


[[('attempt', 1),
  ('biden', 1),
  ('china', 1),
  ('meeting', 1),
  ('taiwan', 1),
  ('xi', 1)]]

### Building the Topic Model

In [55]:
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=25,
                     random_state=100,
                     update_every=1,
                     chunksize=200,
                     passes=200,
                    #  alpha='auto',
                     per_word_topics=True)


In [57]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
# doc_lda = lda_model[corpus]

[(19,
  '0.193*"ukraine" + 0.120*"texas" + 0.066*"putin" + 0.056*"dems" + '
  '0.045*"invasion" + 0.044*"critic" + 0.036*"more_than" + 0.034*"tie" + '
  '0.032*"dog" + 0.022*"agent"'),
 (11,
  '0.190*"star" + 0.073*"taylor_swift" + 0.061*"trial" + 0.035*"email" + '
  '0.034*"harvey_weinstein" + 0.023*"july" + 0.022*"auction" + '
  '0.022*"jennifer" + 0.017*"concert" + 0.015*"place"'),
 (0,
  '0.121*"woman" + 0.067*"threat" + 0.048*"week" + 0.045*"judge" + '
  '0.038*"daughter" + 0.035*"baby" + 0.033*"lawsuit" + 0.033*"concern" + '
  '0.032*"leadership" + 0.031*"boss"'),
 (23,
  '0.196*"china" + 0.078*"taiwan" + 0.034*"hollywood" + 0.032*"board" + '
  '0.030*"halloween" + 0.029*"ceremony" + 0.023*"diagnosis" + 0.020*"freedom" '
  '+ 0.013*"fame" + 0.012*"comedian"'),
 (8,
  '0.110*"time" + 0.094*"crisis" + 0.076*"story" + 0.061*"virginia" + '
  '0.060*"governor" + 0.052*"veteran" + 0.046*"christmas" + 0.042*"battle" + '
  '0.033*"ohio" + 0.023*"immigration"'),
 (3,
  '0.091*"war" + 0.07

##### Notes
* So visually it seems we have a different topics when we use `bigrams`. 

### Analyzing Model

In [58]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -24.6660062486084

Coherence Score:  0.5764826591765325


### Visualize Topics

In [59]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.



PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
21     0.344292  0.086872       1        1  7.024868
15     0.076181 -0.364001       2        1  5.746449
3      0.018726 -0.054749       3        1  5.205032
24    -0.008905 -0.010226       4        1  4.919699
13    -0.012213 -0.006107       5        1  4.735238
1      0.157158  0.046343       6        1  4.697949
5     -0.021731  0.004176       7        1  4.287051
0     -0.021291  0.003721       8        1  4.267493
6     -0.021415  0.003966       9        1  4.193985
8     -0.026620  0.008879      10        1  4.038165
19    -0.022500  0.004985      11        1  3.921261
17    -0.027235  0.009440      12        1  3.863117
2     -0.031869  0.013502      13        1  3.852276
7     -0.026939  0.009168      14        1  3.819380
16    -0.029711  0.011646      15        1  3.791030
14    -0.032467  0.014008      16        1  3.574669
9      0.029590  0.043800      17        1  3.483316
20    -0.039504  0.019531      18        1  3.421442
22    -0.035058  0.016118      19        1  3.416466
18    -0.043124  0.022126      20        1  3.345518
4     -0.042744  0.021865      21        1  3.256846
11    -0.045590  0.023697      22        1  2.949517
10    -0.044907  0.023250      23        1  2.827691
12    -0.046038  0.023985      24        1  2.705209
23    -0.046086  0.024005      25        1  2.656332, topic_info=          Term         Freq        Total Category  logprob  loglift
1        biden  1131.000000  1131.000000  Default  30.0000  30.0000
203      trump   525.000000   525.000000  Default  29.0000  29.0000
432     police   432.000000   432.000000  Default  28.0000  28.0000
689     report   470.000000   470.000000  Default  27.0000  27.0000
9          gop   541.000000   541.000000  Default  26.0000  26.0000
...        ...          ...          ...      ...      ...      ...
6405  optimism     0.078505     1.890422  Topic25  -9.6628   0.4468
1153    russia     0.078505     1.890430  Topic25  -9.6628   0.4468
1482   michael     0.078505     1.890423  Topic25  -9.6628   0.4468
2625      test     0.078505     1.890423  Topic25  -9.6628   0.4468
2202       cnn     0.078505     1.890430  Topic25  -9.6628   0.4468

[846 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
59       18  0.993484     abortion
364      16  0.890863      academy
568      20  0.935936   accusation
582      21  0.961532      accuser
321      15  0.966278          act
...     ...       ...          ...
143      20  0.713139   xi_jinping
160       7  0.993996         year
94       13  0.939099  yellowstone
452      21  0.919493     you_need
457      21  0.803633          zoo

[519 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[22, 16, 4, 25, 14, 2, 6, 1, 7, 9, 20, 18, 3, 8, 17, 15, 10, 21, 23, 19, 5, 12, 11, 13, 24])

## Gensim LDA with Trigram BOW

### Lemmatization

In [37]:
## lemmatization with trigrams
data_words_trigrams = make_trigrams(data_words, bigram_mod, trigram_mod)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
# nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words_trigrams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])


[['biden', 'xi', 'meeting', 'imminent', 'attempt', 'china', 'taiwan']]


### Create Dictionary & Corpus

In [38]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1)]]


In [39]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]


[[('attempt', 1),
  ('biden', 1),
  ('china', 1),
  ('imminent', 1),
  ('meeting', 1),
  ('taiwan', 1),
  ('xi', 1)]]

### Building the Topic Model

In [40]:
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=30,
                     random_state=100,
                     update_every=1,
                     chunksize=200,
                     passes=200,
                    #  alpha='auto',
                     per_word_topics=True)


In [41]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
# doc_lda = lda_model[corpus]

[(3,
  '0.118*"car" + 0.068*"green" + 0.038*"november" + 0.037*"event" + '
  '0.028*"emotional" + 0.026*"jennifer" + 0.025*"newsom" + 0.025*"tennessee" + '
  '0.019*"pete" + 0.016*"dark"'),
 (22,
  '0.145*"gop" + 0.070*"election" + 0.058*"race" + 0.044*"military" + '
  '0.040*"story" + 0.035*"campaign" + 0.034*"democratic" + 0.033*"law" + '
  '0.032*"gov" + 0.032*"senate"'),
 (20,
  '0.211*"day" + 0.130*"time" + 0.083*"leader" + 0.079*"national" + '
  '0.033*"program" + 0.027*"park" + 0.023*"illinois" + 0.018*"ben" + '
  '0.017*"famous" + 0.012*"press"'),
 (23,
  '0.201*"man" + 0.128*"family" + 0.088*"good" + 0.067*"inflation" + '
  '0.027*"night" + 0.025*"comment" + 0.018*"founder" + 0.010*"boyfriend" + '
  '0.008*"cher" + 0.008*"chef"'),
 (21,
  '0.106*"prison" + 0.078*"company" + 0.031*"demand" + 0.018*"mandatory" + '
  '0.013*"mississippi" + 0.007*"shift" + 0.000*"conviction" + '
  '0.000*"therapist" + 0.000*"canada" + 0.000*"extortion"'),
 (0,
  '0.161*"home" + 0.095*"violence" + 

### Analyzing Model

In [42]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -27.97983575510768

Coherence Score:  0.5600343755347889


### Visualize Topics

In [43]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.



PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
22     0.309005 -0.218833       1        1  7.100145
28     0.231971  0.334217       2        1  6.738930
4      0.063033  0.036523       3        1  4.843114
26     0.122645 -0.072220       4        1  4.813064
10     0.077264 -0.060602       5        1  4.216545
18     0.011509  0.015071       6        1  3.920305
9      0.003680  0.012454       7        1  3.630344
17    -0.016244  0.006419       8        1  3.492285
24    -0.017321  0.006068       9        1  3.459093
7     -0.020007  0.005297      10        1  3.364273
12    -0.020382  0.005124      11        1  3.336112
5     -0.023232  0.004424      12        1  3.274075
27     0.001020 -0.025826      13        1  3.204258
20    -0.026507  0.003435      14        1  3.198344
6     -0.030227  0.002488      15        1  3.068371
25    -0.035507  0.001144      16        1  3.066391
14    -0.030169  0.002496      17        1  3.001295
13    -0.036656  0.000901      18        1  2.962009
8     -0.006978 -0.028117      19        1  2.899503
11    -0.040233 -0.000072      20        1  2.886466
23    -0.040528 -0.000192      21        1  2.788711
16    -0.040178 -0.000059      22        1  2.770924
19    -0.043531 -0.000937      23        1  2.661528
15    -0.049399 -0.002373      24        1  2.626210
2     -0.046241 -0.001610      25        1  2.607958
29    -0.052489 -0.003152      26        1  2.493326
1     -0.055634 -0.003983      27        1  2.289108
3     -0.058821 -0.004783      28        1  2.026151
0     -0.064032 -0.006335      29        1  1.771626
21    -0.065811 -0.006968      30        1  1.489534, topic_info=            Term         Freq        Total Category  logprob  loglift
1          biden  1061.000000  1061.000000  Default  30.0000  30.0000
204        trump   546.000000   546.000000  Default  29.0000  29.0000
301          new   543.000000   543.000000  Default  28.0000  28.0000
734       report   496.000000   496.000000  Default  27.0000  27.0000
450       police   437.000000   437.000000  Default  26.0000  26.0000
..           ...          ...          ...      ...      ...      ...
6             xi     0.059047    19.438821  Topic30  -9.3995  -1.5900
7     california     0.059047   136.712278  Topic30  -9.3995  -3.5406
9    competitive     0.059047    11.184648  Topic30  -9.3995  -1.0373
10      election     0.059047   240.591348  Topic30  -9.3995  -4.1058
11           gop     0.059047   495.926024  Topic30  -9.3995  -4.8291

[1206 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
62        2  0.994085     abortion
379      25  0.871053      academy
598      22  0.925704   accusation
614       8  0.966842      accuser
331      19  0.961182          act
...     ...       ...          ...
36        3  0.923172        wrong
6        19  0.925982           xi
163       7  0.993902         year
96        8  0.953975  yellowstone
476       9  0.729979          zoo

[526 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[23, 29, 5, 27, 11, 19, 10, 18, 25, 8, 13, 6, 28, 21, 7, 26, 15, 14, 9, 12, 24, 17, 20, 16, 3, 30, 2, 4, 1, 22])

## Gensim LDA with Spacy noun-chunks n-Grams

##### Notes
* In this case we are trying to use `Spacy's` noun-chunks to create n-grams.
* We'll need to first create tokens from clean text. 
* We'll then need a function to replace the nouns in (noun chunks) with ngram word. 
* The `lemmatize` this, 
    * We'll need to test with and without POS to see if our filtering affects ngrams. 

### Creating Noun Chunks

In [44]:
## Lets start by reviewing noun chunks created by spacy
docs = [create_pos_tag(" ".join(x)) for x in data_words]

### Creating Noun Chunks Ngrams

In [45]:
n_grams = create_noun_chunk_ngrams(docs)
n_grams

[['biden',
  'says',
  'after',
  'xi',
  'meeting',
  'he',
  'doesn',
  'believe',
  'there',
  'is',
  'imminent_attempt',
  'from',
  'china',
  'to',
  'invade',
  'taiwan'],
 ['gop_rep_calvert',
  'wins',
  'election',
  'in',
  'competitive_california_house_seat'],
 ['pelosi',
  'not',
  'even',
  'thinking',
  'about',
  'political_future',
  'before',
  'house_majority',
  'called',
  'spox',
  'says'],
 ['arizona',
  'gov',
  'election',
  'katie_hobbs',
  'defeats',
  'gop_challenger',
  'kari_lake',
  'race',
  'may',
  'now',
  'go',
  'to',
  'recount',
  'under',
  'state_law'],
 ['idaho',
  'quadruple',
  'student',
  'homicide',
  'crime',
  'of',
  'passion',
  'burglary',
  'gone',
  'wrong',
  'among',
  'possible_motives',
  'mayor',
  'says'],
 ['jennifer_siebel_newsom',
  'identifies',
  'harvey_weinstein',
  'as',
  'alleged_rapist',
  'in',
  'emotional_sexual_assault_testimony'],
 ['commanders',
  'hand',
  'eagles',
  'first_loss',
  'of',
  'season',
  'in',

In [46]:
data_lemmatized = lemmatization_without_pos(n_grams)

In [47]:
data_lemmatized

[['biden',
  'say',
  'after',
  'xi',
  'meeting',
  'he',
  'doesn',
  'believe',
  'there',
  'be',
  'imminent_attempt',
  'from',
  'china',
  'to',
  'invade',
  'taiwan'],
 ['gop_rep_calvert',
  'win',
  'election',
  'in',
  'competitive_california_house_seat'],
 ['pelosi',
  'not',
  'even',
  'think',
  'about',
  'political_future',
  'before',
  'house_majority',
  'call',
  'spox',
  'say'],
 ['arizona',
  'gov',
  'election',
  'katie_hobbs',
  'defeat',
  'gop_challenger',
  'kari_lake',
  'race',
  'may',
  'now',
  'go',
  'to',
  'recount',
  'under',
  'state_law'],
 ['idaho',
  'quadruple',
  'student',
  'homicide',
  'crime',
  'of',
  'passion',
  'burglary',
  'go',
  'wrong',
  'among',
  'possible_motive',
  'mayor',
  'say'],
 ['jennifer_siebel_newsom',
  'identify',
  'harvey_weinstein',
  'as',
  'alleged_rapist',
  'in',
  'emotional_sexual_assault_testimony'],
 ['commander',
  'hand',
  'eagle',
  'first_loss',
  'of',
  'season',
  'in',
  'wild_nfc_east

##### Notes
* So since we are doing `lemmatization` without any `POS` some parts of speech words are present in our lemmatized data. 
* Words like `doesn't`, `believe`, `think` etc are present. I think we should update the function to ignore certain `POS` rather than just include all words. 
* Lets do a quick check on how these `POS` are distributed. 

In [48]:
n_gram_pos = [create_pos_tag(" ".join(x)) for x in data_lemmatized]
n_gram_pos_distribution, is_alpha, is_stop = create_pos_tags_distribution(n_gram_pos)

In [49]:
token_distribution_df = pd.DataFrame.from_dict(n_gram_pos_distribution, orient='index', columns=['count']).reset_index().rename(columns={"index": "tags"})
## lets create a distribution of POS tags
## checking the distribution of word count in title
fig = px.histogram(token_distribution_df, x="tags", y="count", title="Distribution POS Tags in Title")
fig.show()

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

d:\workspace\Aletheia\env\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



##### Notes
* Lets see how our `ngrams` are tagged

In [50]:
for token in n_gram_pos:
    for token in token:
        ## Only print the noun chunks
        if("_" in token.text):            
            print(token.text, token.pos_, token.dep_)

imminent_attempt NOUN attr
gop_rep_calvert PROPN nsubj
competitive_california_house_seat PROPN pobj
political_future NOUN pobj
house_majority NOUN dep
katie_hobbs PROPN appos
gop_challenger NOUN dobj
kari_lake PROPN conj
state_law NOUN pobj
possible_motive ADJ amod
jennifer_siebel_newsom PROPN nsubj
harvey_weinstein PROPN dobj
alleged_rapist NOUN pobj
emotional_sexual_assault_testimony NOUN pobj
first_loss NOUN appos
wild_nfc_east_upset NOUN pobj
arizona_gop_rep_schweikert PROPN dep
democratic_challenger PROPN dobj
house_majority PROPN pobj
marjorie_taylor_greene PROPN dep
gop_colleague PROPN pobj
speaker_bad_strategy PROPN pobj
student_loan_buyout_abortion NOUN nsubj
distasteful_rape_comment ADJ dobj
special_warriors_broadcast PROPN pobj
oregons_th_congressional_district ADJ amod
democrat_andrea_salinas PROPN pobj
andy_warhol_art NOUN pobj
kevin_costner PROPN nsubj
yellowstone_national_park PROPN dobj
patriot_awards PROPN npadvmod
honor_heroism NOUN dobj
fox_nation PROPN pobj
this_day

##### Notes
* Looks like most of the noun chunks are tagged as `NOUN`, `PROPN` or `ADJ`, but lets confirm it using visualization. 


In [51]:
noun_chunks_tags = {}
for token in n_gram_pos:
    for token in token:
        ## Only print the noun chunks
        if("_" in token.text):
            ## increment the count of the noun chunk
            noun_chunks_tags[token.pos_] = noun_chunks_tags.get(token.pos_, 0) + 1

noun_chunks_tags

{'NOUN': 8112,
 'PROPN': 8452,
 'ADJ': 714,
 'X': 851,
 'VERB': 74,
 'NUM': 30,
 'ADV': 10,
 'PRON': 56,
 'INTJ': 4,
 'SYM': 4,
 'ADP': 1,
 'DET': 1}

##### Notes
* So as assumed most of them are `NOUN` or `PROPN` but just to make sure we don't loose any chunks, lets modify our lemmatization script to handle this case. 

In [52]:
data_lemmatized = lemmatization_noun_chunks(n_grams)

In [53]:
data_lemmatized

[['biden', 'xi', 'meeting', 'imminent_attempt', 'china', 'taiwan'],
 ['gop_rep_calvert', 'election', 'competitive_california_house_seat'],
 ['pelosi', 'political_future', 'house_majority', 'spox'],
 ['arizona',
  'gov',
  'election',
  'katie_hobbs',
  'gop_challenger',
  'kari_lake',
  'race',
  'recount',
  'state_law'],
 ['idaho',
  'student',
  'homicide',
  'crime',
  'passion',
  'burglary',
  'possible_motive',
  'mayor'],
 ['jennifer_siebel_newsom',
  'harvey_weinstein',
  'alleged_rapist',
  'emotional_sexual_assault_testimony'],
 ['commander', 'eagle', 'first_loss', 'season', 'wild_nfc_east_upset'],
 ['arizona_gop_rep_schweikert',
  'democratic_challenger',
  'republicans',
  'house_majority'],
 ['marjorie_taylor_greene',
  'gop_colleague',
  'mccarthy',
  'speaker_bad_strategy'],
 ['student_loan_buyout_abortion', 'midterm', 'democrats', 'biden', 'critic'],
 ['hall',
  'famer',
  'tim',
  'hardaway',
  'distasteful_rape_comment',
  'special_warriors_broadcast'],
 ['oregons_th

##### Notes
* So the lemmatized data looks promising lets train the model and see. 

### Create Dictionary & Corpus

In [54]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1)]]


In [55]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]


[[('biden', 1),
  ('china', 1),
  ('imminent_attempt', 1),
  ('meeting', 1),
  ('taiwan', 1),
  ('xi', 1)]]

### Building the Topic Model

In [56]:
lda_model = LdaModel(corpus=corpus,
                     id2word=id2word,
                     num_topics=30,
                     random_state=100,
                     update_every=1,
                     chunksize=200,
                     passes=200,
                    #  alpha='auto',
                     per_word_topics=True)


In [57]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
# doc_lda = lda_model[corpus]

[(18,
  '0.079*"america" + 0.020*"fox_nation" + 0.019*"baby" + 0.007*"flight" + '
  '0.006*"kevin_costner" + 0.000*"massive_shift" + 0.000*"nightmare_scenario" '
  '+ 0.000*"mccaul" + 0.000*"nato_majority" + 0.000*"red_line"'),
 (17,
  '0.156*"year" + 0.045*"threat" + 0.027*"life" + 0.010*"kathie_lee_gifford" + '
  '0.007*"cher" + 0.004*"atlanta" + 0.000*"democracy" + 0.000*"massive_shift" '
  '+ 0.000*"possible_threat" + 0.000*"nato_majority"'),
 (20,
  '0.009*"joe_biden" + 0.008*"loss" + 0.006*"chief" + 0.005*"the_nation" + '
  '0.000*"mccaul" + 0.000*"nato_majority" + 0.000*"massive_shift" + '
  '0.000*"quantum_computing_answer" + 0.000*"nuclear_weapons" + '
  '0.000*"possible_threat"'),
 (23,
  '0.027*"veteran" + 0.016*"christmas" + 0.015*"thanksgiving" + '
  '0.014*"tribute" + 0.009*"jeff" + 0.008*"team" + 0.003*"tom_brady" + '
  '0.002*"saturday" + 0.000*"massive_shift" + 0.000*"mccaul"'),
 (10,
  '0.085*"iran" + 0.000*"massive_shift" + 0.000*"red_line" + '
  '0.000*"nuclear_weap

### Analyzing Model

In [58]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -48.68804192741965

Coherence Score:  0.5222654255319291


##### Notes
* So our model didn't perform well, in fact regular model BOW did better than noun chunks. 

### Visualize Topics

In [59]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = gensimvis.prepare(lda_model, corpus, id2word)
vis

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.



PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
13     0.146446 -0.124518       1        1  5.383394
22    -0.147752 -0.123232       2        1  5.279413
12     0.000172  0.033807       3        1  3.997223
7      0.000138  0.026461       4        1  3.959367
17     0.000145  0.028044       5        1  3.818324
28     0.000095  0.017702       6        1  3.599469
9      0.000097  0.018143       7        1  3.562110
11     0.000105  0.019678       8        1  3.539652
1      0.000078  0.014193       9        1  3.475027
8      0.000071  0.012979      10        1  3.420717
4      0.000088  0.016261      11        1  3.398471
14     0.000090  0.016677      12        1  3.372617
15     0.000051  0.009251      13        1  3.322350
29     0.000060  0.011018      14        1  3.238948
18     0.000039  0.007153      15        1  3.200399
26     0.000052  0.009520      16        1  3.173025
6      0.000044  0.008080      17        1  3.145606
21     0.000027  0.005040      18        1  3.135344
2      0.000022  0.004076      19        1  3.014306
23     0.000015  0.002799      20        1  2.999242
24     0.000011  0.002080      21        1  2.973060
0      0.000010  0.001826      22        1  2.970302
5      0.000005  0.001183      23        1  2.941265
27     0.000005  0.000999      24        1  2.915346
10     0.000010  0.002002      25        1  2.810244
25    -0.000007 -0.000969      26        1  2.782167
20    -0.000025 -0.004309      27        1  2.697947
19    -0.000019 -0.003147      28        1  2.697408
3     -0.000032 -0.005407      29        1  2.644502
16    -0.000043 -0.007390      30        1  2.532754, topic_info=            Term        Freq       Total Category  logprob  loglift
0          biden  566.000000  566.000000  Default  30.0000  30.0000
552        trump  282.000000  282.000000  Default  29.0000  29.0000
85       ukraine  183.000000  183.000000  Default  28.0000  28.0000
113         year  185.000000  185.000000  Default  27.0000  27.0000
46     democrats  149.000000  149.000000  Default  26.0000  26.0000
..           ...         ...         ...      ...      ...      ...
16     kari_lake    0.044116   10.784575  Topic30  -9.7827  -1.8232
17   katie_hobbs    0.044116    3.921392  Topic30  -9.7827  -0.8115
18          race    0.044116   48.846987  Topic30  -9.7827  -3.3338
22         crime    0.044116   61.232429  Topic30  -9.7827  -3.5597
28       student    0.044116   39.296899  Topic30  -9.7827  -3.1162

[1242 rows x 6 columns], token_table=      Topic      Freq                   Term
term                                        
432      29  0.820751             accusation
131      15  0.982652                america
213       2  0.916608                 answer
13        8  0.956293                arizona
553      11  0.776839                   army
376       5  0.843243                atlanta
58        8  0.927979                auction
530      13  0.911639                 author
287      19  0.518465              authority
117      15  0.908312                   baby
695      13  0.693719  baby_formula_shortage
259      11  0.954207                 battle
0         1  0.998337                  biden
483      21  0.929532                 bidens
660      22  0.893289            bill_murray
693       7  0.934424                  birth
669      17  0.858994                brother
410      28  0.928670             california
381      13  0.937720                   call
502       9  0.918733                    car
708      22  0.728086                 chance
390       5  0.843451                   cher
440      27  0.754134                  chief
1        17  0.986006                  china
515      20  0.912598              christmas
33       21  0.788694              commander
305      26  0.530893  commanders_dan_snyder
452      21  0.921201                  court
22       14  0.979873                  crime
45        4 

## Sklearn LDA with Count Vectorization

##### Notes
* For Count Vecotorization we'l use SKLearn's LDA algorithm. The algorithm is same as Gensim, but the interface is different and it allows us to use CountVectorizations. 

### Lemmatization

In [48]:
# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words)


print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'attempt', 'china', 'taiwan']]


### Count Vectorizer

In [49]:
vectorizer = CountVectorizer(analyzer='word',       
                             min_df=10,                        # minimum reqd occurences of a word 
                             stop_words='english',             # remove stop words
                             lowercase=True,                   # convert all words to lowercase
                             token_pattern='[a-zA-Z0-9]{3,}',  # num chars > 3
                             # max_features=50000,             # max number of uniq words
                            )

data_vectorized = vectorizer.fit_transform([" ".join(lem_word) for lem_word in data_lemmatized])

In [50]:
# Materialize the sparse data
data_dense = data_vectorized.todense()

# Compute Sparsicity = Percentage of Non-Zero cells
print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")


Sparsicity:  0.41396974461688885 %


### Building Topic Model

In [88]:
# Build LDA Model 35
lda_model = LatentDirichletAllocation(n_components=75,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=128,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                      learning_decay=0.5
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)  # Model attributes

LatentDirichletAllocation(learning_decay=0.5, learning_method='online',
                          n_components=75, n_jobs=-1, random_state=100)


### Analyzing Model

In [89]:
analyze_sklearn_lda_model(lda_model, data_vectorized)
# See model parameters
pprint(lda_model.get_params())

## 
# Log Likelihood:  -237441.44543701067
# Perplexity:  1308.0281367579253

Log Likelihood:  -282557.5307768166
Perplexity:  5114.501965606973
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.5,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 75,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


In [90]:
dominant_topics = print_sklearn_dominant_topics(lda_model, data_vectorized)
dominant_topics

In [91]:
topic_distribution = print_sklearn_topic_distribution(lda_model, data_vectorized)
topic_distribution

Topic  Num Documents
0       1            553
1       3            551
2       6            510
3      30            470
4       0            425
5       7            407
6      11            358
7      27            327
8      44            311
9       8            278
10     41            269
11      5            255
12     59            239
13     22            238
14     46            225
15     26            199
16     24            198
17     13            193
18     51            154
19     33            151
20     32            147
21     56            119
22     21            118
23     12            103
24     48            100
25     52             94
26     61             92
27     31             87
28     54             76
29     42             56
30      9             55
31     71             53
32     47             38
33     72             34
34     37             34
35     28             24
36     60             23
37     69             22
38     19             16
39     62             15
40      2             12
41     15             11
42     23             11
43     34             10
44     18              6
45     17              6
46     25              5
47     10              5
48     67              5
49     20              4
50     36              4
51     14              3
52     65              3
53     66              3
54      4              2
55     38              2
56     73              2
57     74              1
58     40              1
59     35              1
60     70              1
61     68              1
62     64              1
63     57              1
64     43              1

### Visualizing Topics

In [92]:
panel = visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer)
panel

d:\workspace\Aletheia\env\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:800: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:810: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



PreparedData(topic_coordinates=                x           y  topics  cluster      Freq
topic                                                   
30     221.344986  329.500336       1        1  5.530250
44     422.063538  -82.029121       2        1  5.092926
6     -253.933746 -227.311646       3        1  4.127904
46     220.382050  220.398010       4        1  3.953519
41    -156.174240 -283.581421       5        1  3.945924
27     -52.125397 -316.082764       6        1  3.919781
1     -150.902252 -431.434967       7        1  3.344008
7      251.579636 -254.742844       8        1  3.215468
3     -447.145050 -111.948547       9        1  3.108594
11    -224.244507  306.750183      10        1  3.107764
59     297.960266 -151.344345      11        1  2.936271
8     -448.932465  160.089386      12        1  2.819361
26     -14.534152 -421.485565      13        1  2.776254
33     218.709396 -366.923248      14        1  2.762821
22    -270.599579 -356.421326      15        1  2.697300
51    -323.502045 -106.966034      16        1  2.595891
32    -135.201233  240.682892      17        1  2.317485
13    -379.109924 -245.711456      18        1  2.301911
24     444.328461   98.426224      19        1  2.300913
56    -344.425690  287.089355      20        1  2.262189
48     106.080208  288.762878      21        1  2.165787
52     112.308777 -451.837463      22        1  2.074016
5      324.162933  400.351654      23        1  1.889297
61     -75.091095  319.483734      24        1  1.853624
0     -416.597504   24.227758      25        1  1.819904
54    -251.691864   82.549500      26        1  1.643999
42    -224.652176 -132.228348      27        1  1.515477
71      85.372955 -318.508362      28        1  1.454830
31     179.509430  133.427399      29        1  1.225979
69     270.369293  -54.744030      30        1  1.211121
72    -323.483734  155.177109      31        1  1.131239
21     355.108368  246.438812      32        1  1.085609
12    -150.979599  419.913116      33        1  1.037518
62     301.767426  135.690796      34        1  0.823228
9      380.950012 -249.823532      35        1  0.745793
60     341.037323   21.550484      36        1  0.732205
47      10.238615  380.990936      37        1  0.592798
28     233.520065   54.724483      38        1  0.524192
34    -301.082916   -0.745221      39        1  0.485215
37     124.351349  415.965302      40        1  0.484998
67       8.838502  252.368607      41        1  0.455662
19    -130.215515  130.673615      42        1  0.374856
23     -60.429985  181.301758      43        1  0.359574
18     106.899651  187.895630      44        1  0.356307
36     154.532394 -216.773239      45        1  0.348799
43    -122.937759 -186.421661      46        1  0.344959
25      49.342278 -223.092636      47        1  0.330731
66    -209.939194  175.410004      48        1  0.319871
2      185.986038 -117.690880      49        1  0.310777
10      95.406189 -152.007309      50        1  0.309874
17    -142.497101 -105.764717      51        1  0.308220
64     181.549438  -18.413382      52        1  0.306694
40     -48.128822 -143.790482      53        1  0.301872
15     -33.730175 -218.906815      54        1  0.300646
14     118.453499  -78.527580      55        1  0.299856
55    -168.484543   54.017300      56        1  0.296869
49      23.145060  164.796677      57        1  0.290702
35      19.956974 -131.049194      58        1  0.282999
68      72.622879  106.710335      59        1  0.281535
70     111.407890   -9.792500      60        1  0.279081
4       50.271080  -73.896538      61        1  0.278421
57     134.302917   59.607735      62        1  0.278080
38    -207.701843  -29.625526      63        1  0.275087
20    -128.804825  -31.642345      64        1  0.274454
45     -73.049019  -81.872551      65        1  0.273018
29      50.452774  -15.855639      66        1  0.272770
74      -6.355562  103.773193      67        1  0.270693
65     -68.359108   88.539162      6

In [93]:
## vectorizer, lda_model, n_words=20
df_topic_keywords = show_sklearn_topics(vectorizer, lda_model)
formatted_topics = format_sklearn_topics(df_topic_keywords)
formatted_topics

Word 0       Word 1          Word 2      Word 3     Word 4       Word 5        Word 6         Word 7        Word 8        Word 9        Word 10       Word 11         Word 12       Word 13      Word 14      Word 15       Word 16       Word 17       Word 18       Word 19
Topic 0         family       murder          parent     suspect    college   allegation      carolina            dad         north        singer       behavior       killing         robbery  battleground        hotel        scene      document           ted          face          room
Topic 1       election  republicans           claim      charge     theory         week          vote          msnbc           doj       senator        michael          jake            mass          head   leadership       tapper          boss        robert       clinton     mcconnell
Topic 2            pac        super          abbott     partner      party    passenger       patient         patrol          paul         peace         pelosi         pence    pennsylvania      pentagon       people  performance        person          pete  philadelphia         photo
Topic 3         police          man            deal        life        lee       nation       sheriff        taliban       chicago       service         arrest         faith            mike       accuser   prosecutor         park          army          mask        matter      pentagon
Topic 4           reid       abbott         partner       party  passenger      patient        patrol           paul         peace        pelosi          pence  pennsylvania        pentagon        people  performance       person          pete  philadelphia         photo        pickup
Topic 5       abortion        child         country     support       nick       father        newsom         access         model   restriction       audience        supply        kentucky     amendment     survivor        place     responder        cannon         level        ruling
Topic 6          state         time         midterm        poll   campaign      georgia        county          issue         judge     christmas           team           san          walker        voting     williams    francisco         shark        ballot     celebrity      herschel
Topic 7          trump       people         twitter        elon       musk         book          post       congress       scandal        austin       question       defense         adviser   impeachment        maher      council         pence           end       liberal      pressure
Topic 8         bidens       record        democrat      action      queen          joe      district         energy         harry           oil           mark        prison          prince        mother      company         king     criticism       charles        author         today
Topic 9         attack       update           david     jackson       hate         nato        europe    performance        people      pentagon          pence        pelosi           peace          paul       patrol      patient  pennsylvania        person  philadelphia     passenger
Topic 10          raid       abbott         partner       party  passenger      patient        patrol           paul         peace        pelosi          pence  pennsylvania        pentagon        people         park  performance          pete  philadelphia         photo        pickup
Topic 11         death        crime       president        iran      mayor          car           fbi         change         price      lawmaker           host           gas             cop        regime    protester    admission     emergency         rally          hell         truck
Topic 12      michigan  documentary            sign       james   national    commander  organization      halloween           dan         honor        whitmer      language    constitution         candy         alex       disney        snyder       wedding       turnout          star
Topic 13    

##### Notes
* Somehow I couldn't find out `coherence` for but from visualization it seems that the model has created topics which are easy to interpret and not overlapping
* I still see some topics that don't make sense but, we can tweak this further by creating n-grams, including more POS and skipping lemmatization. 

### GridSearch for Params

### Write to Pickle File

In [95]:
# create an iterator object with write permission - model.pkl
features = vectorizer.get_feature_names_out()

path = "../pickles/sklearn_count_vectorization/"

with open(path + '/features_v1', 'wb') as files:
    pickle.dump(features, files)
    
with open(path + '/model_v1', 'wb') as files:
    pickle.dump(lda_model, files)   

## Sklearn LDA with Bi-Grams Count Vectorization

### Lemmatization with Bigrams

In [70]:
## lemmatization with bigrams
data_words_bigrams = make_bigrams(data_words, bigram_mod)


data_lemmatized = lemmatization(data_words_bigrams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'imminent', 'attempt', 'china', 'taiwan']]


In [71]:
data_lemmatized

[['biden', 'xi', 'meeting', 'imminent', 'attempt', 'china', 'taiwan'],
 ['gop',
  'rep',
  'calvert',
  'election',
  'competitive',
  'california',
  'house',
  'seat'],
 ['pelosi', 'political', 'future', 'house', 'majority', 'spox'],
 ['arizona',
  'gov',
  'election',
  'gop',
  'challenger',
  'race',
  'recount',
  'state',
  'law'],
 ['idaho',
  'student',
  'homicide',
  'crime',
  'passion',
  'burglary',
  'wrong',
  'possible',
  'motive',
  'mayor'],
 ['jennifer', 'siebel', 'newsom', 'rapist', 'emotional', 'testimony'],
 ['commander', 'eagles', 'loss', 'season', 'wild', 'nfc', 'east', 'upset'],
 ['arizona',
  'gop',
  'rep',
  'schweikert',
  'democratic',
  'challenger',
  'republicans',
  'house',
  'majority'],
 ['marjorie',
  'taylor',
  'greene',
  'gop',
  'colleague',
  'mccarthy',
  'speaker',
  'bad',
  'strategy'],
 ['buyout', 'abortion', 'midterm', 'democrats', 'biden', 'critic'],
 ['hall',
  'famer',
  'tim',
  'hardaway',
  'distasteful',
  'rape',
  'comment',


### Count Vectorizer

In [72]:
vectorizer = CountVectorizer(analyzer='word',       
                             min_df=10,                        # minimum reqd occurences of a word 
                             stop_words='english',             # remove stop words
                             lowercase=True,                   # convert all words to lowercase
                             token_pattern='[a-zA-Z0-9]{3,}',  # num chars > 3
                             # max_features=50000,             # max number of uniq words
                            )

data_vectorized = vectorizer.fit_transform([" ".join(lem_word) for lem_word in data_lemmatized])

In [73]:
# Materialize the sparse data
data_dense = data_vectorized.todense()

# Compute Sparsicity = Percentage of Non-Zero cells
print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")


Sparsicity:  0.39075112722766375 %


### Building Topic Model

In [74]:
# Build LDA Model 35
lda_model = LatentDirichletAllocation(n_components=33,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=128,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)  # Model attributes

LatentDirichletAllocation(learning_method='online', n_components=33, n_jobs=-1,
                          random_state=100)


### Analyzing Model

In [75]:
analyze_sklearn_lda_model(lda_model, data_vectorized)

# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -216628.62659080783
Perplexity:  1449.4553342887064
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 33,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


### Visualizing Topics

In [76]:
dominant_topics = print_sklearn_dominant_topics(lda_model, data_vectorized)
dominant_topics

In [77]:
topic_distribution = print_sklearn_topic_distribution(lda_model, data_vectorized)
topic_distribution

Topic  Num Documents
0       1            888
1       0            592
2       3            590
3      14            532
4       4            532
5       2            519
6       5            466
7      27            333
8      11            312
9       8            301
10     19            294
11      9            260
12     29            235
13     16            227
14     23            188
15     28            155
16     18            154
17     10            150
18     13            137
19     24            130
20     20            117
21     31            104
22     22            101
23     32             97
24     26             68
25      7             68
26     17             55
27     30             43
28     25             19
29     12             17
30     21             15
31     15             15
32      6              5

In [78]:
panel = visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer)
panel

d:\workspace\Aletheia\env\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:800: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:810: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



PreparedData(topic_coordinates=                x           y  topics  cluster      Freq
topic                                                   
14      -8.440456   90.149948       1        1  6.284583
27    -137.038803  -52.116375       2        1  5.673662
29     146.141403  169.368118       3        1  5.524074
1     -136.767929   28.056456       4        1  5.468919
19     196.323929 -125.734802       5        1  4.647795
4       58.820442  140.294312       6        1  4.555965
2       59.228130   62.402313       7        1  4.146597
3      -79.468018   76.570572       8        1  4.126733
23     110.345886 -128.916473       9        1  3.961788
28     210.854919   59.768673      10        1  3.821620
11     -91.822350 -229.005783      11        1  3.782273
5     -125.597343 -142.703461      12        1  3.551582
31    -123.440041  155.322418      13        1  3.286328
24     -44.415028 -158.762253      14        1  3.274865
16    -216.386703   -6.412930      15        1  3.265090
8      208.688339  -31.097879      16        1  3.257783
32    -204.522064 -107.480278      17        1  3.242887
18      11.242757 -234.749268      18        1  2.951610
9       39.909458 -156.380966      19        1  2.890396
0      128.710709  -57.965359      20        1  2.479196
20      22.445618  214.086868      21        1  2.469576
22     124.893288   11.836060      22        1  2.397793
13     111.213120 -211.575562      23        1  2.105356
26     130.216415   86.183571      24        1  2.087274
10    -186.032623   91.658569      25        1  1.952104
30     -41.507648  157.507614      26        1  1.934169
17     -70.172028   -2.621508      27        1  1.525525
7      -68.811028  -77.715607      28        1  1.240251
25      -2.757716  -99.584312      29        1  1.022638
21      53.263062   -5.383107      30        1  0.856850
12      55.783127  -68.777847      31        1  0.832579
15      -8.929082  -36.549698      32        1  0.738762
6       -6.708246   22.086742      33        1  0.643377, topic_info=          Term        Freq       Total Category  logprob  loglift
80       biden  564.000000  564.000000  Default  30.0000  30.0000
736     report  260.000000  260.000000  Default  29.0000  29.0000
599        new  267.000000  267.000000  Default  28.0000  28.0000
216        day  221.000000  221.000000  Default  27.0000  27.0000
901      trump  250.000000  250.000000  Default  26.0000  26.0000
..         ...         ...         ...      ...      ...      ...
321      fight    0.118656   20.568145  Topic33  -7.3863  -0.1091
802     silent    0.118656   15.020468  Topic33  -7.3863   0.2053
683  president    0.118656   96.124530  Topic33  -7.3863  -1.6510
746   rhetoric    0.118656   12.089710  Topic33  -7.3863   0.4223
474        kid    0.118656   89.475529  Topic33  -7.3863  -1.5793

[1236 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
0        11  0.931169          abc
1        14  0.992460     abortion
2        19  0.966655        abuse
4        18  0.933546       access
5        17  0.944626      account
...     ...       ...          ...
976      15  0.952317  yellowstone
977       8  0.954146        young
978      18  0.919145     youngkin
979       5  0.893193       zeldin
980       4  0.938388    zelenskyy

[861 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[15, 28, 30, 2, 20, 5, 3, 4, 24, 29, 12, 6, 32, 25, 17, 9, 33, 19, 10, 1, 21, 23, 14, 27, 11, 31, 18, 8, 26, 22, 13, 16, 7])

In [79]:
## vectorizer, lda_model, n_words=20
df_topic_keywords = show_sklearn_topics(vectorizer, lda_model)
formatted_topics = format_sklearn_topics(df_topic_keywords)
formatted_topics

Word 0        Word 1       Word 2        Word 3        Word 4       Word 5      Word 6         Word 7         Word 8       Word 9         Word 10      Word 11      Word 12      Word 13      Word 14        Word 15     Word 16       Word 17     Word 18       Word 19
Topic 0     military       veteran         life      congress      michigan         john       study        teacher           cnns          fox        americas         nick        troop        james          tom          datum       honor  announcement    personal         ready
Topic 1    democrats       midterm        voter       russian     president          gop      leader          video       campaign  afghanistan          critic     violence         drug       battle        power          owner     program        career         use         obama
Topic 2       senate          race    candidate         state       georgia        final  washington           mark          major       nevada         control         role   prosecutor       center        close        warnock   secretary          real        line  battleground
Topic 3         year   republicans        covid        medium          case      yearold       party           news        taliban        young            girl          old      nominee         list    mcconnell          night     hearing      williams        long          date
Topic 4        biden        bidens       record        hunter        energy     district      speech          chris            joe          oil  administration     business          cop         head  immigration  congressional    evidence      domestic       title       foreign
Topic 5         star         child       family        parent        murder      country     support            way        suspect        photo       christmas          doc       father      service        point      celebrity     illegal  relationship      doctor           set
Topic 6        levin    defamation         love  relationship          woke       victim        nick  congressional        prolife         idea            hard      russian         fake    emotional       parent          local    facility          navy         end      upcoming
Topic 7         free        summer          lee          mike      pentagon          god         jan          faith       jennifer      apology       emotional  independent       newsom         riot       winner     vulnerable     wedding       capitol       focus          utah
Topic 8       border        crisis      migrant        policy      virginia     shooting    response        federal          probe   university             ban      assault         test     official       harris         weapon    football        player       cuomo         fight
Topic 9          key       primary       health         trial        tiktok        court       viral     allegation        massive      husband          secret         rule        abuse    community       lawyer          pound         bid        couple    marriage         spike
Topic 10      report        office  transgender       surgery          rise        coach        film       sanction    antisemitic       cartel           trend        voice      failure        drama     minister          minor      relief          nets      regime      maralago
Topic 11       trump           cnn       people       twitter          book      scandal    question         austin           post      defense         adviser       social    criticism  impeachment       result            nbc      moment         truth     capitol         pence
Topic 12         dad          mask        fauci       mexican          face      robbery       guest           drug            man      morning          hochul         city        party       answer         week        russias       guide           bob    platform      americas
Topic 13         mom         story      officer           job      daughter     security         fan        

### Write to Pickle File

In [80]:
# create an iterator object with write permission - model.pkl
features = vectorizer.get_feature_names_out()

path = "../pickles/sklearn_count_vectorization_bigrams/"

with open(path + '/features_v1', 'wb') as files:
    pickle.dump(features, files)
    
with open(path + '/model_v1', 'wb') as files:
    pickle.dump(lda_model, files)   

## SKLearn LDA with noun-chunks n-grams

### Creating Noun Chunks

In [81]:
## Lets start by reviewing noun chunks created by spacy
docs = [create_pos_tag(" ".join(x)) for x in data_words]

### Creating Noun Chunks N-grams

In [82]:
n_grams = create_noun_chunk_ngrams(docs)

In [83]:
## lemmatization with bigrams
# data_words_bigrams = make_bigrams(data_words, bigram_mod)

# data_words_trigrams = make_trigrams(data_words, bigram_mod, trigram_mod)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
# nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
## performaing lemmatization with noun chunks to preserve the ngram words. 
# data_lemmatized = lemmatization_noun_chunks(n_grams)
data_lemmatized = lemmatization(n_grams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'china', 'taiwan']]


In [84]:
data_lemmatized

[['biden', 'xi', 'meeting', 'china', 'taiwan'],
 ['election'],
 ['pelosi', 'spox'],
 ['arizona', 'gov', 'election', 'race', 'recount'],
 ['idaho',
  'student',
  'homicide',
  'crime',
  'passion',
  'burglary',
  'wrong',
  'mayor'],
 [],
 ['commander', 'eagle', 'season'],
 ['republicans'],
 ['mccarthy'],
 ['midterm', 'democrats', 'biden', 'critic'],
 ['hall', 'famer', 'tim', 'hardaway'],
 [],
 ['mercedes', 'auction'],
 ['november'],
 ['history', 'love'],
 ['walker', 'start'],
 [],
 ['record'],
 ['republicans', 'willing'],
 ['ukraine', 'taiwan', 'xi'],
 ['door', 'official'],
 ['disappointed'],
 ['decade'],
 ['biden', 'summit', 'indonesia', 'concern'],
 [],
 ['tribute', 'nt'],
 ['worth', 'year'],
 [],
 ['baby', 'flight'],
 [],
 ['arizona'],
 [],
 ['america', 'violence'],
 ['paint', 'traffic', 'unhelpful'],
 ['twitter', 'people', 'austin'],
 ['mississippi', 'demand'],
 ['arizona', 'rancher', 'ms'],
 [],
 ['broadway', 'lawsuit', 'white'],
 ['greg', 'gutfeld'],
 [],
 ['republicans', 'demo

### Count Vectorizer

In [85]:
vectorizer = CountVectorizer(analyzer='word',       
                             min_df=10,                        # minimum reqd occurences of a word 
                             stop_words='english',             # remove stop words
                             lowercase=True,                   # convert all words to lowercase
                             token_pattern='[a-zA-Z0-9]{3,}',  # num chars > 3
                             # max_features=50000,             # max number of uniq words
                            )

data_vectorized = vectorizer.fit_transform([" ".join(lem_word) for lem_word in data_lemmatized])

In [86]:
# Materialize the sparse data
data_dense = data_vectorized.todense()

# Compute Sparsicity = Percentage of Non-Zero cells
print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")


Sparsicity:  0.32756994386503624 %


### Building Topic Model

In [87]:
# Build LDA Model 35
lda_model = LatentDirichletAllocation(n_components=33,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=128,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)  # Model attributes

LatentDirichletAllocation(learning_method='online', n_components=33, n_jobs=-1,
                          random_state=100)


### Analyzing Model

In [88]:
analyze_sklearn_lda_model(lda_model, data_vectorized)

# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -34671.21402862915
Perplexity:  285.73554488924265
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 33,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


### Visualizing Topics

In [89]:
dominant_topics = print_sklearn_dominant_topics(lda_model, data_vectorized)
dominant_topics

In [90]:
topic_distribution = print_sklearn_topic_distribution(lda_model, data_vectorized)
topic_distribution

Topic  Num Documents
0       0           3835
1       1            486
2      31            204
3       4            163
4       5            157
5      11            145
6      12            144
7      14            138
8      29            137
9      21            137
10     10            132
11     22            126
12      7            126
13     19            123
14      8            116
15      6            115
16     20            107
17     23            102
18     17            101
19     13            101
20     24             98
21     32             98
22     30             94
23      9             90
24      2             86
25     18             83
26     15             81
27     27             78
28     16             73
29     28             72
30      3             61
31     26             56
32     25             54

In [91]:
panel = visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer)
panel

d:\workspace\Aletheia\env\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:800: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:810: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



PreparedData(topic_coordinates=                x           y  topics  cluster      Freq
topic                                                   
1     -128.943893  -65.541389       1        1  6.719991
31     120.114670  -71.778297       2        1  5.386487
29    -135.123810    6.740100       3        1  4.083119
12     -22.106522  125.171402       4        1  3.655083
21     137.287216    0.169824       5        1  3.558482
30    -105.847099   68.653862       6        1  3.288795
5      -73.778252  -78.064629       7        1  3.229397
11      93.252983   22.534081       8        1  3.176407
23     -85.815063   22.386641       9        1  3.136175
14     -44.290096 -131.640152      10        1  3.125417
24     -59.063766   86.226700      11        1  3.105301
20     101.667397   70.824814      12        1  3.096447
10     -25.800537  -89.231972      13        1  3.077845
22     -10.545510  -52.490055      14        1  3.018195
32     -13.571925   74.619278      15        1  2.961496
4       68.853592  -99.611809      16        1  2.915963
13     -87.228889  -25.058809      17        1  2.839012
19      28.146875  106.921951      18        1  2.817575
27      24.098869  -73.321655      19        1  2.774061
16      17.985403   50.655277      20        1  2.769420
7       17.350475 -117.883141      21        1  2.743906
17      52.363285   30.178976      22        1  2.689634
6       91.549400  -25.590900      23        1  2.677848
0      -47.005405  -39.380836      24        1  2.600101
8       55.443027   72.416107      25        1  2.555791
15      58.058327  -51.213570      26        1  2.512005
28     -13.627728   27.575529      27        1  2.436724
18      52.908298   -8.831724      28        1  2.392685
25     -47.210403   42.484215      29        1  2.340763
9      -46.528347    1.137592      30        1  2.202939
2       20.543976  -28.852673      31        1  2.095289
3      -12.403473  -12.187575      32        1  2.019271
26      17.981123    8.902758      33        1  1.998378, topic_info=          Term        Freq       Total Category  logprob  loglift
15       biden  259.000000  259.000000  Default    30.00  30.0000
62   democrats  123.000000  123.000000  Default    29.00  29.0000
239       year  109.000000  109.000000  Default    28.00  28.0000
214      trump  128.000000  128.000000  Default    27.00  27.0000
218    ukraine   99.000000   99.000000  Default    26.00  26.0000
..         ...         ...         ...      ...      ...      ...
95    governor    0.039098   16.639771  Topic33    -8.05  -2.1407
234        way    0.039098   21.579986  Topic33    -8.05  -2.4006
8       arrest    0.039098   15.319833  Topic33    -8.05  -2.0580
123   majority    0.039098   22.349639  Topic33    -8.05  -2.4357
165    protest    0.039098   18.956700  Topic33    -8.05  -2.2710

[1707 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
0        19  0.984071       abortion
1        11  0.980935    afghanistan
2        31  0.926760          alarm
3        18  0.984914        america
4        10  0.977957      americans
5        18  0.889866         answer
6        28  0.956924            aoc
7         8  0.932342        arizona
8        30  0.913848         arrest
9        14  0.964151         attack
10       20  0.919432        auction
11       15  0.919019           baby
12        1  0.934423       backlash
13        2  0.944294            bad
14        8  0.941540         battle
15        1  0.997043          biden
16        3  0.901134         bidens
17       30  0.911594            big
18       25  0.939191          birth
19       11  0.948663           book
20        9  0.951084         border
21       21  0.927673     california
22       33  0.965064       campaign
23       13  0.897383            car
24        4  0.945568        carlson
25       24  0.955004           case
26       12  0.897566            cdc
27        1  0.921524         charge
28        8  0.902809 

In [92]:
## vectorizer, lda_model, n_words=20
df_topic_keywords = show_sklearn_topics(vectorizer, lda_model)
formatted_topics = format_sklearn_topics(df_topic_keywords)
formatted_topics

Word 0       Word 1      Word 2        Word 3         Word 4        Word 5      Word 6       Word 7        Word 8         Word 9       Word 10    Word 11     Word 12      Word 13     Word 14    Word 15    Word 16     Word 17    Word 18     Word 19
Topic 0     inflation     reporter        case  pennsylvania            tie          kyiv    mccarthy       racist          wife        midterm          race   question    shooting     majority         nyc        fbi        dog         cop     police   halloween
Topic 1         biden     congress         war        taiwan      president        charge    backlash       crisis          deal          china         msnbc       home   fetterman   republican      update     europe      ready   zelenskyy      alarm     america
Topic 2      thousand        alarm      source        doctor  investigation    republican        hour  coronavirus         ready            fbi         death      china         war       taiwan      silent      video   fentanyl      expert       year   christmas
Topic 3          poll       debate        open         issue         taylor           big         god      midterm         crime         police      majority    warnock         gop      yearold        hour   official        dad        time     senate       alarm
Topic 4          year        judge      silent         pound            lot       lawsuit       group  republicans         ready          alarm         issue       life      border          war       woman      china       hour     florida       cher   zelenskyy
Topic 5       midterm       parent      critic        office           july       warnock      walker    democrats         biden         silent         trump     decade        case      economy    november  inflation   mccarthy      russia  democracy        plan
Topic 6     fetterman        texas      family         photo            dad      fentanyl    michigan        email           man            car      abortion     threat     ukraine        today     georgia       book  important       child  protester        case
Topic 7           day        covid  california       concern            cop     protester        help        biden       georgia     washington      election  important        poll         news    backlash   fentanyl        fox        love       safe       trump
Topic 8         woman      florida     taliban         birth    afghanistan   republicans         aoc        trump      question           iran          life       dems    mccarthy         year       right     bidens        gop       state      house         bad
Topic 9           man     governor      arrest     christmas          cuomo  thanksgiving         big         cher         obama          death      abortion   backlash      letter      suspect         fbi      birth     source        race     europe      people
Topic 10    democrats       record       obama           car     washington   republicans     economy     congress        result       november      backlash     border    virginia        voter     midterm   election  protester  reelection    auction      tiktok
Topic 11         iran        video     arizona       protest       shooting    university    virginia       battle     criticism           cher          year    history     suspect       victim     student     border   official         gop    migrant   education
Topic 12  republicans      support    question        tucker          party       carlson         son          doj        father          trump           tie    economy        teen     election        dems       plan    midterm      threat   november  california
Topic 13          gop        putin        test      shanghai          drive        number       issue          dem          poll            war         crime        law         bad      georgia       msnbc      covid       book    question   response        dead
Topic 14       police         time   americans        murder         p

### Write to Pickle File

In [93]:
# create an iterator object with write permission - model.pkl
features = vectorizer.get_feature_names_out()

path = "../pickles/sklearn_count_vectorization_noun_chunks"

with open(path + '/features_v1', 'wb') as files:
    pickle.dump(features, files)
    
with open(path + '/model_v1', 'wb') as files:
    pickle.dump(lda_model, files)    

## SKLearn with Tri-Grams

In [94]:
## lemmatization with bigrams
# data_words_bigrams = make_bigrams(data_words, bigram_mod)

data_words_trigrams = make_trigrams(data_words, bigram_mod, trigram_mod)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
# nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
## performaing lemmatization with noun chunks to preserve the ngram words. 
data_lemmatized = lemmatization_noun_chunks(data_words_trigrams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'attempt', 'china', 'taiwan']]


In [95]:
data_lemmatized

[['biden', 'xi', 'meeting', 'attempt', 'china', 'taiwan'],
 ['gop', 'rep', 'calvert', 'election', 'california', 'house', 'seat'],
 ['pelosi', 'future', 'house', 'majority', 'spox'],
 ['arizona',
  'gov',
  'election',
  'katie_hobbs',
  'gop',
  'challenger',
  'kari_lake',
  'race',
  'recount',
  'state',
  'law'],
 ['idaho',
  'student',
  'homicide',
  'crime',
  'passion',
  'burglary',
  'motive',
  'mayor'],
 ['jennifer',
  'siebel',
  'newsom',
  'harvey_weinstein',
  'rapist',
  'sexual_assault',
  'testimony'],
 ['commander', 'eagles', 'loss', 'season', 'wild', 'nfc', 'east', 'upset'],
 ['arizona',
  'gop',
  'rep',
  'schweikert',
  'challenger',
  'republicans',
  'house',
  'majority'],
 ['marjorie',
  'taylor',
  'greene',
  'gop',
  'colleague',
  'mccarthy',
  'speaker',
  'bad',
  'strategy'],
 ['student_loan',
  'buyout',
  'abortion',
  'midterm',
  'democrats',
  'biden',
  'critic'],
 ['hall',
  'famer',
  'tim',
  'hardaway',
  'rape',
  'comment',
  'special',
  

### Count Vectorizer

In [96]:
vectorizer = CountVectorizer(analyzer='word',       
                             min_df=10,                        # minimum reqd occurences of a word 
                             stop_words='english',             # remove stop words
                             lowercase=True,                   # convert all words to lowercase
                             token_pattern='[a-zA-Z0-9]{3,}',  # num chars > 3
                             # max_features=50000,             # max number of uniq words
                            )

data_vectorized = vectorizer.fit_transform([" ".join(lem_word) for lem_word in data_lemmatized])

In [97]:
# Materialize the sparse data
data_dense = data_vectorized.todense()

# Compute Sparsicity = Percentage of Non-Zero cells
print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")


Sparsicity:  0.4063710841443506 %


### Building Topic Model

In [47]:
# Build LDA Model 35
lda_model = LatentDirichletAllocation(n_components=33,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=128,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)  # Model attributes

NameError: name 'data_vectorized' is not defined

### Analyzing Model

In [99]:
analyze_sklearn_lda_model(lda_model, data_vectorized)

# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -239448.82377936013
Perplexity:  1170.1017032659263
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 33,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


### Visualizing Topics

In [100]:
dominant_topics = print_sklearn_dominant_topics(lda_model, data_vectorized)
dominant_topics

In [101]:
topic_distribution = print_sklearn_topic_distribution(lda_model, data_vectorized)
topic_distribution

Topic  Num Documents
0       1            733
1       0            719
2       2            642
3      10            515
4       3            423
5       6            407
6      18            378
7       7            370
8       4            310
9       5            297
10     19            264
11     22            213
12     14            210
13      9            207
14     16            197
15     24            193
16     31            184
17     25            153
18     26            149
19     21            148
20     27            142
21     30            118
22      8            115
23     17            109
24     23            106
25     13             82
26     11             77
27     32             73
28     15             72
29     28             43
30     12             30
31     29             24
32     20             16

In [102]:
panel = visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer)
panel

d:\workspace\Aletheia\env\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:800: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:810: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



PreparedData(topic_coordinates=               x          y  topics  cluster      Freq
topic                                                 
10    -48.919239  -6.560654       1        1  5.290027
1     -76.166542  -9.485081       2        1  5.143586
18    -42.161819 -30.160267       3        1  5.119954
19    -61.560291  20.161993       4        1  4.395120
7     -20.547855 -73.373222       5        1  4.287313
6      42.657387  54.159672       6        1  4.276563
2     -59.494904  46.049797       7        1  4.231072
31     63.092125  28.903294       8        1  3.993138
22    -32.848267  38.553291       9        1  3.847977
0      47.102688 -55.161568      10        1  3.765510
3      41.606979 -20.812984      11        1  3.682147
24    -34.928986 -52.961620      12        1  3.631491
25    -27.789194  68.657478      13        1  3.311973
16     -9.278261  54.291599      14        1  3.276927
14     -4.074765 -50.408905      15        1  3.256721
21     65.272270 -27.642876      16        1  3.236050
4     -33.235867  14.516580      17        1  3.141900
26     60.697521   0.734041      18        1  3.028033
30     13.447790  37.045918      19        1  3.013138
23    -65.420425 -42.243137      20        1  2.809026
27     16.625397 -67.385681      21        1  2.787877
5      15.111651  65.908096      22        1  2.787014
9      34.946251  26.932556      23        1  2.508664
17     24.585428 -39.293068      24        1  2.317379
8     -17.276979 -28.724840      25        1  2.017943
32     34.247829   4.949896      26        1  1.736686
11      5.365294 -28.092175      27        1  1.695333
28     -8.912347  29.023096      28        1  1.691115
15    -24.295820  -7.494877      29        1  1.495035
13     18.897181 -10.370337      30        1  1.338506
12     11.329117  12.065025      31        1  1.101292
29     -1.645489  -8.162411      32        1  0.932863
20     -9.515964   8.701823      33        1  0.852626, topic_info=         Term        Freq       Total Category  logprob  loglift
90      biden  603.000000  603.000000  Default  30.0000  30.0000
439     house  280.000000  280.000000  Default  29.0000  29.0000
793    report  234.000000  234.000000  Default  28.0000  28.0000
987     trump  256.000000  256.000000  Default  27.0000  27.0000
294  election  241.000000  241.000000  Default  26.0000  26.0000
..        ...         ...         ...      ...      ...      ...
286     drone    0.050971   32.780174  Topic33  -8.6429  -1.7017
440     human    0.050971   31.511563  Topic33  -8.6429  -1.6623
393     guard    0.050971   13.425189  Topic33  -8.6429  -0.8090
883    source    0.050971   27.927942  Topic33  -8.6429  -1.5415
521      lake    0.050971   20.779465  Topic33  -8.6429  -1.2459

[1167 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
0        12  0.967941     abbott
1        25  0.943479        abc
2         1  0.295540   abortion
2         3  0.703384   abortion
3         3  0.972414     abrams
...     ...       ...        ...
1070     17  0.946731   youngkin
1071     12  0.039435     zeldin
1071     21  0.907012     zeldin
1072      7  0.947387  zelenskyy
1073     15  0.955474     zucker

[950 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[11, 2, 19, 20, 8, 7, 3, 32, 23, 1, 4, 25, 26, 17, 15, 22, 5, 27, 31, 24, 28, 6, 10, 18, 9, 33, 12, 29, 16, 14, 13, 30, 21])

In [103]:
## vectorizer, lda_model, n_words=20
df_topic_keywords = show_sklearn_topics(vectorizer, lda_model)
formatted_topics = format_sklearn_topics(df_topic_keywords)
formatted_topics

Word 0       Word 1       Word 2      Word 3        Word 4        Word 5     Word 6    Word 7     Word 8        Word 9     Word 10      Word 11         Word 12        Word 13     Word 14      Word 15     Word 16       Word 17      Word 18      Word 19
Topic 0      police          man  coronavirus        city          case     inflation  americans     study  christmas          team      austin      chicago          number       pandemic      arrest       msnbcs        loss       comment        dozen   girlfriend
Topic 1      border     official      migrant     climate        crisis        pelosi     expert       dem     policy       officer     protest       change        activist       lawmaker      mother       meghan      prince        cancer      illegal     southern
Topic 2     ukraine          war    president     florida         world          deal    veteran     month     nation       message    invasion       battle        national         effort     service        putin         air      americas      soldier        agent
Topic 3    election      midterm         time      bidens        record         money    liberal      mark      group       husband        dark      network             jim        clinton    evidence         cash     prolife           aid      manchin      politic
Topic 4       white        video     campaign    virginia        member         queen   response      king      owner           jan     charles        probe      university            ban   criticism    committee      weapon        sister        heart  performance
Topic 5      report         star          way     concern        oregon         putin    netflix       doc     chinas        regime      center         role        american        hearing   celebrity       summit    williams        doctor         fear        coach
Topic 6       biden        china          fbi      taiwan         admin           cop     source   meeting      kanye         point         win    commander            wave          years   reduction     backlash      matter           red  documentary          dan
Topic 7       house          gop          rep  california          dems         mayor   majority   primary        tim          ohio        ryan         seat          season        handout       kelly       letter     suicide      governor   challenger         work
Topic 8      speech    education       voting         job          drug    department        use     visit    missile     supporter      island          nbc          alaska           rise      reform          cbs        greg        choice        fauci       cartel
Topic 9       woman        child          nyc     support         board          nick    taliban     human     father  relationship         kim      attempt           model     kardashian      cannon      silence       kabul        secret         hate         flag
Topic 10      court      supreme         iran      recipe        taylor           roe      swift      baby       paul          wade    abortion          tom          tiktok         ruling        teen          act  allegation      decision         food         jeff
Topic 11     threat     security        chief     defense          mass      hospital     flight     surge     travel       warning      putins       stroke            site    controversy     scooter        braun   passenger       atlanta       equity         mile
Topic 12     action       prison      company      effect          oped         scene      jason   buffalo     killer       custody      stance       demand        employee           exec       paper        saudi     prolife         admin        biden      opinion
Topic 13       test        drive        harry      olivia        styles         wilde       film      shia       bear       labeouf       worry        drama           rumor        darling       paper         jeep       opens         jason       office          mom
Topic 14        cnn        covid      

### Write to Pickle File

In [104]:
# create an iterator object with write permission - model.pkl
features = vectorizer.get_feature_names_out()

path = "../pickles/sklearn_count_vectorization_trigrams"

with open(path + '/features_v1', 'wb') as files:
    pickle.dump(features, files)
    
with open(path + '/model_v1', 'wb') as files:
    pickle.dump(lda_model, files)   

## SKLearn LDA with TF-IDF Vectorization

##### Notes
* Earlier in the LDA we saw that there were a lot of terms with significantly higher frequency than the mean. 
* One theory is that these high frequency words might be biasing the topics, so we are going to use `TF-IDF` vectorization technique to see if we can fix that bias. 

### Lemmatization

In [63]:
# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'attempt', 'china', 'taiwan']]


### TF-IDF Vectorization

In [158]:
## helper function to create tfidf matrix
def create_tfidf_matrix(data, max_features=1000):
    tfidf_vectorizer = TfidfVectorizer(max_features=max_features, max_df=0.95, min_df=2, stop_words='english')
    tfidf_matrix = tfidf_vectorizer.fit_transform(data)
    return tfidf_matrix, tfidf_vectorizer

In [159]:
## create tfidf matrix
data_vectorized, vectorizer = create_tfidf_matrix([" ".join(lem_word) for lem_word in data_lemmatized])

### Building Topic Model

In [201]:

# Build LDA Model 35
lda_model = LatentDirichletAllocation(n_components=33,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=128,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)

LatentDirichletAllocation(learning_method='online', n_components=33, n_jobs=-1,
                          random_state=100)


### Analyzing Model

In [202]:
analyze_sklearn_lda_model(lda_model, data_vectorized)

# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -193615.76075850287
Perplexity:  7032.809323372056
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 33,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


### Visualizing Topics

In [203]:
## vectorizer, lda_model, n_words=20
df_topic_keywords = show_sklearn_topics(vectorizer, lda_model)
formatted_topics = format_sklearn_topics(df_topic_keywords)
formatted_topics

Word 0        Word 1       Word 2     Word 3       Word 4      Word 5     Word 6       Word 7      Word 8     Word 9         Word 10       Word 11        Word 12       Word 13      Word 14      Word 15    Word 16      Word 17     Word 18    Word 19
Topic 0           mom         story     daughter        job      wedding        bear       skin       camera       birth    stelter        lockdown        cotton           plan          hour          row       effort      video       cannon       psaki      claim
Topic 1         biden     democrats      midterm   election  republicans        time   abortion          gop       voter  inflation           trump    washington          house         right         dems         week       post    christmas         sen     critic
Topic 2        russia        pelosi       expert        dem       health       party      chris      senator  reelection    sanders         michael           bid        brother     wisconsin          run  impeachment     driver      ukraine    colorado   opponent
Topic 3          wife        battle        casey     johnny         work    pentagon       debt       ground        depp     brooks           garth        appeal          amber    quarantine       trisha      handout      email        court     justice        rep
Topic 4    withdrawal           aoc  anniversary  instagram          arm      bernie       book        china    security  direction           crime   afghanistan          voter        crisis        actor        gaffe      elvis         song      leader  criticism
Topic 5          home            uk        kevin      point         tech      spacey   minister        heche        oped        max             tip         grand    celebration         harry          man          doc   memorial         case     anthony     museum
Topic 6        attack           fox         news     recipe         test  journalist      power      control     concern    economy           drive          jeff          visit     celebrity          cup         idea    chicken      pumpkin  government       july
Topic 7        border         house      migrant      white       leader         gop        rep  afghanistan       biden   virginia            paul       teacher        assault        harris        admin        trial    primary       harvey    majority       rape
Topic 8     president        parent        world       deal     reporter      murder       ford     shooting      nation    college         message         board          drone        mother      soldier  yellowstone      actor      suspect        view      trump
Topic 9    california        member         role   birthday      netflix         doc  diagnosis       secret       guard         st           coast  backtoschool          squad            ms    christina        state       life          aoc    maralago      woman
Topic 10      anthony       article      capitol      story        space      leader       jeff        pound     husband         vp          action        regime          press  independence        sport     marriage       love        model      police        jay
Topic 11        child     americans    candidate       poll        photo        vote    support       charge       voter       nick          debate           jan       mccarthy           gop       update      speaker      model     strategy        mike     cannon
Topic 12      florida       project     desantis   democrat      lincoln    district       game       family          la      brian            ryan           act           ohio          race   republican       school      kelly      surgery         gov        ron
Topic 13        trump        people       taylor    twitter         elon       swift       musk        issue    congress       book           msnbc       scandal          cuomo         maher       friend        heart     moment       decade       award       rock
Topic 14       medium        hunter      stelter       

In [204]:
panel = visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer)
panel

d:\workspace\Aletheia\env\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:800: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:810: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



PreparedData(topic_coordinates=                x           y  topics  cluster      Freq
topic                                                   
23    -112.763939 -114.967010       1        1  8.461446
1     -102.787270  112.073418       2        1  6.791692
7       -8.156545 -117.912476       3        1  5.439683
15     124.122536   78.783401       4        1  4.958148
30     -80.808235   58.072483       5        1  4.938441
18      66.461731   47.631939       6        1  4.878485
8      -56.240158  -34.137325       7        1  4.626480
13      87.466957  -54.873272       8        1  4.186751
12    -144.089172   58.398506       9        1  4.053564
6      -61.860096 -155.117966      10        1  3.746136
11       6.222757 -173.068512      11        1  3.427219
25      65.978683 -143.307373      12        1  3.364920
31    -153.810425   -3.625873      13        1  3.341212
27     118.365067 -105.194290      14        1  2.898674
2     -162.077042  -67.819473      15        1  2.884532
29     -42.341648  137.854691      16        1  2.810219
22      72.895538  111.750542      17        1  2.635440
17      19.021910  141.041977      18        1  2.525926
19     147.285599  -39.190437      19        1  2.521003
24     125.250038   17.140236      20        1  2.354197
32     -31.918722   80.304802      21        1  2.148169
28      42.387444  -88.447083      22        1  1.885459
9      -94.728394    5.923800      23        1  1.719336
5       22.670673   78.111816      24        1  1.636912
3      -11.651003  -16.940680      25        1  1.611552
0     -103.639282  -50.572918      26        1  1.606279
14     -56.543976  -87.242180      27        1  1.562193
26      73.157494   -4.774826      28        1  1.433195
4       -8.513075  -64.249855      29        1  1.267909
10      -4.834939   37.071377      30        1  1.113538
20      32.390930  -37.158821      31        1  1.096508
16     -43.889515   16.278160      32        1  1.053343
21      26.488403    8.620094      33        1  1.021440, topic_info=        Term        Freq       Total Category  logprob  loglift
993     year  114.000000  114.000000  Default  30.0000  30.0000
48   anthony   82.000000   82.000000  Default  29.0000  29.0000
232      day  116.000000  116.000000  Default  28.0000  28.0000
562   medium   78.000000   78.000000  Default  27.0000  27.0000
589      mom   75.000000   75.000000  Default  26.0000  26.0000
..       ...         ...         ...      ...      ...      ...
668    peace    0.171691   11.289304  Topic33  -7.1704   0.3980
890    thing    0.171691   19.716406  Topic33  -7.1704  -0.1596
520      liz    0.171691   12.638635  Topic33  -7.1704   0.2851
933      use    0.171691   16.041316  Topic33  -7.1704   0.0467
875      tax    0.171691   13.921623  Topic33  -7.1704   0.1885

[1371 rows x 6 columns], token_table=      Topic      Freq       Term
term                            
0         6  0.888323     abbott
1         1  0.240441   abortion
1         2  0.531500   abortion
1        11  0.037964   abortion
1        17  0.177167   abortion
...     ...       ...        ...
996       1  0.932747       york
996       7  0.041455       york
997      13  0.917740     zeldin
998       7  0.917693  zelenskyy
999      18  0.874844     zucker

[995 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[24, 2, 8, 16, 31, 19, 9, 14, 13, 7, 12, 26, 32, 28, 3, 30, 23, 18, 20, 25, 33, 29, 10, 6, 4, 1, 15, 27, 5, 11, 21, 17, 22])

### Write to Pickle File

In [198]:
# create an iterator object with write permission - model.pkl
features = vectorizer.get_feature_names_out()

path = "../pickles/sklearn_tfidf_vectorization"

with open(path + '/features_v1', 'wb') as files:
    pickle.dump(features, files)
    
with open(path + '/model_v1', 'wb') as files:
    pickle.dump(lda_model, files)    

## SKLearn LDA with Bigrams TF-IDF Vectorization

### Lemmatization

In [205]:
## lemmatization with bigrams
data_words_bigrams = make_bigrams(data_words, bigram_mod)


data_lemmatized = lemmatization(data_words_bigrams)

# Remove Stop Words
## we are removing stop words in the lemmatization function using spacy is_stop flag
# data_words_nostops = remove_stopwords(data_lemmatized)

print(data_lemmatized[:1])

[['biden', 'xi', 'meeting', 'attempt', 'china']]


### TF-IDF Vectorization

In [222]:
## helper function to create tfidf matrix
def create_tfidf_matrix(data, max_features=1000):
    tfidf_vectorizer = TfidfVectorizer(max_features=max_features, max_df=0.95, stop_words='english')
    tfidf_matrix = tfidf_vectorizer.fit_transform(data)
    return tfidf_matrix, tfidf_vectorizer

In [223]:
## create tfidf matrix
data_vectorized, vectorizer = create_tfidf_matrix([" ".join(lem_word) for lem_word in data_lemmatized])

### Building Topic Model

In [224]:

# Build LDA Model 35
lda_model = LatentDirichletAllocation(n_components=33,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=200,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)

LatentDirichletAllocation(batch_size=200, learning_method='online',
                          n_components=33, n_jobs=-1, random_state=100)


### Analyzing Model

In [225]:
analyze_sklearn_lda_model(lda_model, data_vectorized)

# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -171560.9979676168
Perplexity:  6450.33039842024
{'batch_size': 200,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 33,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


### Visualizing Topics

In [226]:
## vectorizer, lda_model, n_words=20
df_topic_keywords = show_sklearn_topics(vectorizer, lda_model)
formatted_topics = format_sklearn_topics(df_topic_keywords)
formatted_topics

Word 0       Word 1     Word 2        Word 3        Word 4      Word 5        Word 6      Word 7       Word 8      Word 9    Word 10         Word 11       Word 12       Word 13   Word 14       Word 15        Word 16        Word 17      Word 18      Word 19
Topic 0        border       crisis    migrant      governor        bidens       biden          ford       texas  immigration      alaska     harris          agenda          term          mike     tesla       yearold           kemp           town       pickup          jan
Topic 1          year     election      death        medium          dems      leader          week       party    christmas        vote     mother            ohio           day           gop   nominee        author     leadership          trump         boss    mcconnell
Topic 2      democrat     michigan   district           son           gov  republican            la   cofounder    wisconsin          ny       race            rock         james          help    result         pound     nomination        johnson        house     comedian
Topic 3        recipe         case        nyc            ad      hospital        song          idea     pumpkin         head     chicken      album           surge        center       manchin      fall          feud       maryland         dinner     football     incident
Topic 4      congress        shark      whale        boston         space     funeral           gen          ii      station        fish      china            city  philadelphia        voting  election         force       thousand        officer       crisis          suv
Topic 5           war    president      biden        energy       ukraine         joe           oil        mass      michael        nato         tv           coach     zelenskyy          site  takeover          cost           body       colorado        voice       lesson
Topic 6         state          law        gun          team          news    question         judge       right       ballot      county      night        abortion        person          hand   machine          cher            age       resident      morning     watchdog
Topic 7   republicans  coronavirus      house         biden         admin     arizona      majority         sen          gop       media     effort  administration       control           win     price        summer          agent          trump       senate       mexico
Topic 8      official       parent     record    california      virginia     veteran           sex      speech      message    shooting     policy       education       suspect        source   soldier           doj          money        assault       nation       voting
Topic 9         times       member      music         white      movement     darling         field       press        panic  transition   coverage       nashville        artist      festival  location           aoc          biden         school      arizona       voting
Topic 10          gop          rep    primary       teacher        oregon  reelection       college       trump         wade   community    indiana       democrats        effect    challenger    tapper         house         trumps       youngkin          tom       cheney
Topic 11       expert          dem    justice        pelosi       handout       tweet           bid     release   government     hearing     george            date      opponent       jackson    answer          tour           debt  massachusetts       driver        biden
Topic 12       senate         race  democrats       midterm     candidate   fetterman          poll     history       theory      debate    georgia           voter         study  pennsylvania     biden          john  investigation        meeting   washington     thousand
Topic 13          day        child        nyt           mom       support        book     inflation      ruling     daughter    abortion     number            teen         movie       holiday   scandal      

In [227]:
panel = visualize_sklearn_lda_model(lda_model, data_vectorized, vectorizer)
panel

d:\workspace\Aletheia\env\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning:

Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.

d:\workspace\Aletheia\env\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning:

In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:800: FutureWarning:

The default initialization in TSNE will change from 'random' to 'pca' in 1.2.

d:\workspace\Aletheia\env\lib\site-packages\sklearn\manifold\_t_sne.py:810: FutureWarning:

The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.



PreparedData(topic_coordinates=                x           y  topics  cluster      Freq
topic                                                   
12      98.570305  -68.383545       1        1  5.547958
23      70.754059   47.579636       2        1  4.933097
7       64.029282  -57.437187       3        1  4.817244
8      -69.125961   78.407341       4        1  4.746027
18      53.636520   11.829364       5        1  4.728167
26     115.038116  -24.996727       6        1  4.374395
13      90.885315   12.015067       7        1  4.078295
1       44.044559   78.047729       8        1  4.047162
30     -31.925156  100.457573       9        1  3.833657
22     -58.657963    7.367761      10        1  3.508676
0      -98.832069   -5.613303      11        1  3.458149
29     -63.016472  -90.787758      12        1  3.309877
17      46.766453 -103.957748      13        1  3.208067
6       75.908699  101.770241      14        1  3.113635
3      130.936707   24.441870      15        1  2.974738
11      -3.296465  -95.552460      16        1  2.928191
2      -86.558464   37.540142      17        1  2.868811
27      -0.507681   72.489914      18        1  2.842251
5       30.711878   44.943619      19        1  2.839578
24     -32.176495  -62.959129      20        1  2.747133
10      70.721992  -23.432348      21        1  2.688600
15     108.089760   67.079056      22        1  2.632222
28     -71.329727  -40.966171      23        1  2.614233
32     -39.303627   48.867012      24        1  2.530893
19      25.977467  -65.131065      25        1  2.361442
25      16.892637  112.777466      26        1  2.013425
31      33.119339  -24.144306      27        1  1.949993
9       -1.249164  -43.014523      28        1  1.713980
4      -33.789345  -22.776751      29        1  1.511518
16      -3.642585   36.737724      30        1  1.510903
14     -22.328587   11.304322      31        1  1.240933
20       0.642201  -10.485225      32        1  1.205464
21      19.673847   11.532383      33        1  1.121283, topic_info=          Term        Freq       Total Category  logprob  loglift
672     police  142.000000  142.000000  Default  30.0000  30.0000
897       time  100.000000  100.000000  Default  29.0000  29.0000
681       post  105.000000  105.000000  Default  28.0000  28.0000
233       deal  105.000000  105.000000  Default  27.0000  27.0000
413       host   75.000000   75.000000  Default  26.0000  26.0000
..         ...         ...         ...      ...      ...      ...
729     record    0.138727   42.201322  Topic33  -7.3657  -1.2270
525  louisiana    0.138727    7.725698  Topic33  -7.3657   0.4709
334  fisherman    0.138727   10.844236  Topic33  -7.3657   0.1318
969        way    0.138727   33.732362  Topic33  -7.3657  -1.0030
668     player    0.138727   15.234909  Topic33  -7.3657  -0.2081

[1299 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
0        20  0.796160          abc
1         1  0.196380     abortion
1         3  0.034655     abortion
1         5  0.103966     abortion
1         7  0.288795     abortion
...     ...       ...          ...
995      11  0.912342      yearold
996      24  0.924562  yellowstone
997      21  0.918323     youngkin
998      11  0.805473       zeldin
999      19  0.887818    zelenskyy

[1070 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[13, 24, 8, 9, 19, 27, 14, 2, 31, 23, 1, 30, 18, 7, 4, 12, 3, 28, 6, 25, 11, 16, 29, 33, 20, 26, 32, 10, 5, 17, 15, 21, 22])

### Write to Pickle File

In [228]:
# create an iterator object with write permission - model.pkl
features = vectorizer.get_feature_names_out()

path = "../pickles/sklearn_tfidf_bigram_vectorization"

with open(path + '/features_v1', 'wb') as files:
    pickle.dump(features, files)
    
with open(path + '/model_v1', 'wb') as files:
    pickle.dump(lda_model, files)    

## Random Testing

##### Notes
* Lets just do a quick test with the models that just saved to `pickle files` 
* In order to do that we need to take the texts through following steps, 
    * `Tokenize`
    * `Create Noun Chunks`
    * `Create Noun Chunks n-grams`
    * `Lemmatization`
    * `Count Vectorization`
    * `LDA Transform`

### Utiliy Functions

In [123]:
# helper function to load the model and features
def load_pickle_files(path):
    with open(path + '/model_v1', 'rb') as model:
        lda = pickle.load(model)

    # assuming you pickled the vectorizer
    with open(path + '/features_v1', 'rb') as vocab:
        features = pickle.load(vocab)
    return (lda, features)


def create_noun_chunks(data_words):
    docs = [create_pos_tag(" ".join(x)) for x in data_words]
    return docs

In [124]:
# with open('../pickles/noun_chunks_model_v1', 'rb') as model:
#     lda = pickle.load(model)

# # assuming you pickled the vectorizer
# with open('../pickles/noun_chunks_features_v1', 'rb') as vocab:
#     features = pickle.load(vocab)

In [125]:
def predict_topics(text, model, features):
    # tokenize the text
    # print("tokenizing the text...")
    data_words = list(sent_to_words(text))

    # create noun chunks
    # print("creating noun chunks...")
    docs = create_noun_chunks(data_words)

    # create noun chunks ngrams
    # print("creating noun chunk ngrams...")
    n_grams = create_noun_chunk_ngrams(docs)

    # lemmatization
    # print("lemmatization noun chunks...")
    data_lemmatized = lemmatization_noun_chunks(n_grams)

    # count vectorization
    # print("count vectorization...")
   
    vectorizer = CountVectorizer(vocabulary=features)
    # column names
    topicnames = ["Topic" + str(i) for i in range(model.n_components)]
    # print(topicnames)
    
    data_vectorized = vectorizer.fit_transform([" ".join(lem_word) for lem_word in data_lemmatized])

    ## Create a dataframe with topics as rows and features as columns
    ## each cell represents the weight of the feature in the topic
    df_topic_keywords = pd.DataFrame(model.components_)
    df_topic_keywords.columns = vectorizer.get_feature_names_out()
    df_topic_keywords.index = topicnames  # type: ignore
    
    topic_keywords = show_sklearn_topics(vectorizer, model)
    ## transform gives us the topic distribution for each document
    ## here we have a list of probabilities for each topic, index of the list is the topic number
    topic_probability_scores = model.transform(data_vectorized)
    
    ## from the dataframe we then select the row with the highest probability
    topic = df_topic_keywords.iloc[np.argmax(topic_probability_scores), :].values.tolist()  # type: ignore
    topic_list = list(topic_keywords)[np.argmax(topic_probability_scores)]
    topic.sort(reverse=True)    
    features_with_weights = list(zip(topic_list, topic))
    return features_with_weights

### Test Data

In [232]:
random_text = data.sample(1)["cleaned_soft_title"].tolist()
random_text

['bidens white house victory fueled by recordshattering m in dark money report says']

## Random Testing SKLearn Count Vectorization

### Load Model

In [127]:
(lda_count_vectorization, features_count_vectorization) = load_pickle_files("../pickles/sklearn_count_vectorization")

In [129]:

# import time
# for text in random_text:
#     print(text)
#     features_with_weights = predict_topics(text, lda_count_vectorization, features_count_vectorization)
#     print(features_with_weights)
#     print(" ")

features_with_weights = predict_topics(random_text, lda_count_vectorization, features_count_vectorization)
print(random_text)
print(features_with_weights)

['john lennon and yoko ono documentary above us only sky explores the making of imagine']
[('michigan', 36.52623930425795), ('documentary', 27.447596327970306), ('sign', 23.573507613143377), ('james', 22.72751972365308), ('national', 18.840704193920008), ('commander', 18.48258883082548), ('organization', 17.7741395260535), ('halloween', 17.029460419909423), ('dan', 16.926639780475043), ('honor', 11.996944582368089), ('whitmer', 10.697454875562435), ('language', 10.322660429749238), ('constitution', 9.385426670340761), ('candy', 8.01625485555494), ('alex', 7.602328877788677), ('disney', 5.993637758381095), ('snyder', 5.291587159167218), ('wedding', 0.013333333333333343), ('turnout', 0.013333333333333341), ('star', 0.013333333333333336)]


## Random Testing Count Vectorization With BiGrams

### Load Model

In [130]:
(lda_with_bigrams, features_with_bigrams) = load_pickle_files("../pickles/sklearn_count_vectorization_bigrams")

In [131]:
features_with_weights = predict_topics(random_text, lda_with_bigrams, features_with_bigrams)
print(random_text)
print(features_with_weights)

['john lennon and yoko ono documentary above us only sky explores the making of imagine']
[('new', 286.2008404297915), ('florida', 98.29933113494585), ('times', 46.2688818394332), ('great', 41.834539027427596), ('member', 40.46054147428452), ('effort', 36.40575221562433), ('second', 29.09201316999133), ('gubernatorial', 28.21282963311418), ('netflix', 27.685125664936223), ('homeless', 24.734445971035978), ('past', 23.722125650454295), ('mexico', 21.996183147713552), ('laptop', 21.786709878190482), ('documentary', 19.73006268441618), ('divorce', 19.605646236648752), ('alaska', 19.583764393198575), ('spending', 18.423090086388292), ('term', 16.9199165522095), ('album', 16.67155475270202), ('song', 16.138917408236814)]


## Random Testing Count Vectorization With Tri-Grams

### Load Model

In [132]:
(lda_with_trigrams, features_with_trigrams) = load_pickle_files("../pickles/sklearn_count_vectorization_trigrams")

In [133]:
features_with_weights = predict_topics(random_text, lda_with_trigrams, features_with_trigrams)
print(random_text)
print(features_with_weights)

['john lennon and yoko ono documentary above us only sky explores the making of imagine']
[('biden', 653.3658543399711), ('china', 121.6932335355264), ('fbi', 55.531969524502166), ('taiwan', 54.1991196307564), ('admin', 53.246977466464614), ('cop', 30.913455826152433), ('source', 29.170465015592143), ('meeting', 25.211333567996395), ('kanye', 24.61186555780234), ('point', 23.31596523185247), ('win', 23.0603678289169), ('commander', 22.938899845825272), ('wave', 20.734705657150137), ('years', 20.69154295405901), ('reduction', 20.058593422381197), ('backlash', 19.9638638480455), ('matter', 19.799550129538215), ('red', 19.733319827988193), ('documentary', 19.730062806368522), ('dan', 19.72780729204434)]


## Random Testing Count Vectorization With Noun Chunks

### Load Model

In [231]:
(lda_with_noun_chunks, features_with_noun_chunks) = load_pickle_files("../pickles/sklearn_count_vectorization_noun_chunks")

In [135]:
features_with_weights = predict_topics(random_text, lda_with_noun_chunks, features_with_noun_chunks)
print(random_text)
print(features_with_weights)

['john lennon and yoko ono documentary above us only sky explores the making of imagine']
[('inflation', 31.97835950316819), ('reporter', 20.343575134418064), ('case', 18.801041854375427), ('pennsylvania', 15.014314598593383), ('tie', 14.547062191251774), ('kyiv', 11.779298522079308), ('mccarthy', 11.176689304057263), ('racist', 10.10170242087449), ('wife', 9.384304052456438), ('midterm', 0.030303123322411127), ('race', 0.030303111811333796), ('question', 0.030303110608972006), ('shooting', 0.030303107291097992), ('majority', 0.0303031043839695), ('nyc', 0.03030310427583053), ('fbi', 0.030303104270783945), ('dog', 0.030303102507749945), ('cop', 0.03030310242372673), ('police', 0.030303102316094777), ('halloween', 0.030303102116574453)]


## Random Testing TF-IDF Vectorizer

In [199]:
(lda_tf_idf, features_tf_idf) = load_pickle_files("../pickles/sklearn_tfidf_vectorization")

In [200]:
features_with_weights = predict_topics(random_text, lda_tf_idf, features_tf_idf)
print(random_text)
print(features_with_weights)

['cheesy toasty baked egg cups with chives try the recipe']
[('report', 79.73491297632896), ('child', 62.452119047079606), ('baby', 32.07130470825605), ('nick', 24.789656785669894), ('cancer', 22.269333285476332), ('marriage', 16.48714199853262), ('program', 16.21946449782597), ('cannon', 15.616652408954888), ('model', 13.71780077987751), ('divorce', 13.649241341261476), ('skin', 12.114180761689745), ('surgery', 11.976386172652457), ('announcement', 11.044327607639621), ('trend', 9.345856510624623), ('school', 7.12675030456695), ('mom', 4.621294065421706), ('grant', 3.979423611001241), ('idea', 2.017448320850062), ('son', 1.824379365383184), ('race', 1.3314883499576002)]


## Random Testing Bigram TF-IDF Vectorizer

In [233]:
(lda_tf_idf, features_tf_idf) = load_pickle_files("../pickles/sklearn_tfidf_bigram_vectorization")

In [234]:
features_with_weights = predict_topics(random_text, lda_tf_idf, features_tf_idf)
print(random_text)
print(features_with_weights)

['bidens white house victory fueled by recordshattering m in dark money report says']
[('report', 107.08802238714942), ('award', 72.47998799622847), ('protest', 40.80387812058857), ('photo', 34.854444125417906), ('voter', 33.203420456207624), ('tiktok', 31.35847680570265), ('climate', 30.71819642926736), ('job', 27.483208796821675), ('activist', 25.989063181544285), ('economy', 24.08119997877714), ('american', 20.477610430312996), ('thing', 19.616383221149285), ('power', 19.3203427249815), ('dc', 18.7285758218902), ('hero', 17.232864666709737), ('union', 16.592847782383128), ('evidence', 15.501361432056926), ('backlash', 14.885561034346308), ('crash', 14.638223441433427), ('ceremony', 13.608106602835438)]
